<a href="https://colab.research.google.com/github/dany444/one/blob/main/Another_One_2233.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
!pip install pymupdf chardet

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 20.0/20.0 MB 77.7 MB/s eta 0:00:00


**Для проверки**

In [3]:
def detect_encoding_manually(byte_data):
    if byte_data.startswith(b'\xef\xbb\xbf'):
        return 'UTF-8 с BOM'
    if byte_data.startswith(b'\xff\xfe'):
        return 'UTF-16 LE'
    if byte_data.startswith(b'\xfe\xff'):
        return 'UTF-16 BE'

    # Проверка на UTF-8 без BOM
    try:
        byte_data.decode('utf-8')
        return 'UTF-8 без BOM'
    except UnicodeDecodeError:
        pass

    # Проверка на ASCII
    if all(byte <= 0x7F for byte in byte_data):
        return 'ASCII'

    # Проверка на Windows-1251
    try:
        byte_data.decode('windows-1251')
        return 'Windows-1251'
    except UnicodeDecodeError:
        pass

    # Проверка на Windows-1252
    try:
        byte_data.decode('windows-1252')
        return 'Windows-1252'
    except UnicodeDecodeError:
        pass

    return 'Неизвестная кодировка'

# Пример использования
byte_data = b'\xef\xbb\xbfHello, World!'  # UTF-8 с BOM
print(detect_encoding_manually(byte_data))  # Выведет: UTF-8 с BOM

byte_data = b'\xff\xfefile content'  # UTF-16 LE
print(detect_encoding_manually(byte_data))  # Выведет: UTF-16 LE

byte_data = b'Hello, World!'  # ASCII
print(detect_encoding_manually(byte_data))  # Выведет: ASCII

byte_data = b'\xd0\x9f\xd0\xb0\xd1\x80\xd0\xb0\xd0\xbc\xd0\xb5\xd1\x82\xd1\x80'  # Windows-1251
print(detect_encoding_manually(byte_data))  # Выведет: Windows-1251

UTF-8 с BOM
UTF-16 LE
UTF-8 без BOM
UTF-8 без BOM


**Сама проверка**

In [ ]:
import os

def test_encoding_detection():
    base_dir = ''
    test_files = {
        #os.path.join(base_dir, "WINDOWS1251_endPDF (1).pdf"): "UTF-8 с BOM",
        #os.path.join(base_dir, "UTF_RusInLaTeX_1.txt"): "UTF-8 без BOM",
        #os.path.join(base_dir, "_UTF-16LE_RusInLaTeX_1.txt"): "UTF-16 LE",
        #os.path.join(base_dir, "UTF_8 with BOM_RusInLaTeX_1.txt"): "UTF-16 BE",
        #os.path.join(base_dir, "converted.pdf"): "Windows-1251",
        #os.path.join(base_dir, "endPDF_Courier (1).pdf"): "Windows-1252",
        os.path.join(base_dir, "endPDF_Courier (1).pdf"): "Windows-1251",
        os.path.join(base_dir, "converted.pdf"): "UTF-8 без BOM",
    }

    for filename, expected in test_files.items():
        with open(filename, 'rb') as f:
            byte_data = f.read()
            detected = detect_encoding_manually(byte_data)
            print(f"Файл: {filename}, Ожидаемая кодировка: {expected}, Обнаруженная кодировка: {detected}")

if __name__ == "__main__":
    test_encoding_detection()

Файл: endPDF_Courier (1).pdf, Ожидаемая кодировка: Windows-1251, Обнаруженная кодировка: Windows-1251
Файл: converted.pdf, Ожидаемая кодировка: UTF-8 без BOM, Обнаруженная кодировка: UTF-8 без BOM


**Перекодировка**

In [6]:
!pip install pymupdf

import fitz  # PyMuPDF
import chardet
import io

def convert_text_from_windows1251_to_utf8(text: bytes) -> str:
    # Проверяем текущую кодировку текста
    detected_encoding = chardet.detect(text)['encoding']
    if detected_encoding == 'windows-1251':
        return text.decode('windows-1251').encode('utf-8').decode('utf-8')
    return text.decode('utf-8')

def convert_pdf(input_pdf_path: str, output_pdf_path: str):
    # Открываем исходный PDF файл
    pdf_document = fitz.open(input_pdf_path)

    for page_num in range(len(pdf_document)):
        page = pdf_document.load_page(page_num)
        text_instances = page.get_text("dict")["blocks"]

        for block in text_instances:
            if block["type"] == 0:  # 0 - текстовый блок
                for line in block["lines"]:
                    for span in line["spans"]:
                        # Конвертируем текст из Windows-1251 в UTF-8
                        span["text"] = convert_text_from_windows1251_to_utf8(span["text"].encode('utf-8'))

    # Сохраняем измененный PDF файл
    pdf_document.save(output_pdf_path)
    pdf_document.close()

if __name__ == "__main__":
    input_pdf_path = "final_pdf_with_text (8).pdf"  # Путь к исходному PDF файлу
    output_pdf_path = "converted.pdf"  # Путь к конвертированному PDF файлу

    convert_pdf(input_pdf_path, output_pdf_path)
    print(f"PDF файл успешно конвертирован и сохранен как {output_pdf_path}")

PDF файл успешно конвертирован и сохранен как converted.pdf


In [7]:
!pip install pymupdf easyocr
import fitz  # PyMuPDF
import tkinter as tk
from tkinter import filedialog, scrolledtext
import easyocr

class PDFEditor:
    def __init__(self, root):
        self.root = root
        self.root.title("Редактор PDF")

        self.load_pdf_button = tk.Button(root, text="Открыть PDF", command=self.load_pdf)
        self.load_pdf_button.pack()

        self.edit_button = tk.Button(root, text="Внести правки", command=self.extract_text, state=tk.DISABLED)
        self.edit_button.pack()

        self.save_button = tk.Button(root, text="Закончить и сохранить", command=self.save_pdf, state=tk.DISABLED)
        self.save_button.pack()

        self.text_frame = tk.Frame(root)
        self.text_frame.pack()

        self.encoded_text = scrolledtext.ScrolledText(self.text_frame, width=50, height=20)
        self.encoded_text.pack(side=tk.LEFT, padx=5)

        self.decoded_text = scrolledtext.ScrolledText(self.text_frame, width=50, height=20)
        self.decoded_text.pack(side=tk.RIGHT, padx=5)

        self.pdf_path = ""
        self.text_blocks = []

    def load_pdf(self):
        self.pdf_path = filedialog.askopenfilename(filetypes=[("PDF files", "*.pdf")])
        if self.pdf_path:
            self.edit_button.config(state=tk.NORMAL)

    def extract_text(self):
        if not self.pdf_path:
            return

        doc = fitz.open(self.pdf_path)
        self.text_blocks = []

        reader = easyocr.Reader(["en", "ru"])

        full_text = ""

        for page in doc:
            img = page.get_pixmap()
            text_result = reader.readtext(img.tobytes(), detail=0)

            page_text = "\n".join(text_result)
            self.text_blocks.append(page_text)
            full_text += page_text + "\n\n"

        self.encoded_text.delete(1.0, tk.END)
        self.encoded_text.insert(tk.END, full_text)

        self.decoded_text.delete(1.0, tk.END)
        self.decoded_text.insert(tk.END, full_text)

        self.save_button.config(state=tk.NORMAL)

    def save_pdf(self):
        if not self.pdf_path:
            return

        new_text = self.encoded_text.get(1.0, tk.END)
        new_pdf_path = "kopiy_" + self.pdf_path.split("/")[-1]

        doc = fitz.open(self.pdf_path)

        for page_num, page in enumerate(doc):
            page.clean_contents()
            page.insert_text((50, 50), new_text.split("\n\n")[page_num], fontsize=12)

        doc.save(new_pdf_path)
        doc.close()

        self.root.quit()

if __name__ == "__main__":
    root = tk.Tk()
    app = PDFEditor(root)
    root.mainloop()


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.9/2.9 MB 26.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 93.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 70.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 42.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 12.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 5.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 61.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 422.9/422.9 kB 26.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9

TclError: no display name and no $DISPLAY environment variable

In [9]:
!pip install pdfplumber
import fitz  # PyMuPDF
import ipywidgets as widgets
from IPython.display import display
import pdfplumber

class PDFEditor:
    def __init__(self):
        self.pdf_path = ""
        self.text_blocks = []

        self.upload_button = widgets.FileUpload(accept='.pdf', multiple=False)
        self.upload_button.observe(self.load_pdf, names='value')

        self.edit_button = widgets.Button(description="Внести правки", disabled=True)
        self.edit_button.on_click(self.extract_text)

        self.save_button = widgets.Button(description="Закончить и сохранить", disabled=True)
        self.save_button.on_click(self.save_pdf)

        self.encoded_text = widgets.Textarea(layout=widgets.Layout(width='50%'))
        self.decoded_text = widgets.Textarea(layout=widgets.Layout(width='50%'))

        display(self.upload_button, self.edit_button, self.save_button)
        display(widgets.HBox([self.encoded_text, self.decoded_text]))

    def load_pdf(self, change):
        if self.upload_button.value:
            self.pdf_path = list(self.upload_button.value.keys())[0]
            self.edit_button.disabled = False

    def extract_text(self, event):
        if not self.pdf_path:
            return

        with pdfplumber.open(self.pdf_path) as pdf:
            self.text_blocks = [page.extract_text() or "" for page in pdf.pages]

        full_text = "\n\n".join(self.text_blocks)

        self.encoded_text.value = full_text
        self.decoded_text.value = full_text

        self.save_button.disabled = False

    def save_pdf(self, event):
        if not self.pdf_path:
            return

        new_text = self.encoded_text.value
        new_pdf_path = "kopiy_" + self.pdf_path

        doc = fitz.open()

        for page_text in new_text.split("\n\n"):
            page = doc.new_page()
            page.insert_text((50, 50), page_text, fontsize=12)

        doc.save(new_pdf_path)
        doc.close()

        print(f"Файл сохранён как {new_pdf_path}")

if __name__ == "__main__":
    app = PDFEditor()


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.5/42.5 kB 1.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.2/48.2 kB 2.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.5/59.5 kB 4.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.6/5.6 MB 54.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.9/2.9 MB 75.8 MB/s eta 0:00:00


FileUpload(value={}, accept='.pdf', description='Upload')

Button(description='Внести правки', disabled=True, style=ButtonStyle())

Button(description='Закончить и сохранить', disabled=True, style=ButtonStyle())

In [12]:
import fitz  # PyMuPDF
import ipywidgets as widgets
from IPython.display import display
import pdfplumber
import os

class PDFEditor:
    def __init__(self, pdf_url=None):
        self.pdf_path = ""
        self.text_blocks = []

        self.upload_button = widgets.FileUpload(accept='.pdf', multiple=False)
        self.upload_button.observe(self.load_pdf, names='value')

        self.edit_button = widgets.Button(description="Внести правки", disabled=True)
        self.edit_button.on_click(self.extract_text)

        self.save_button = widgets.Button(description="Закончить и сохранить", disabled=True)
        self.save_button.on_click(self.save_pdf)

        self.encoded_text = widgets.Textarea(layout=widgets.Layout(width='50%'))
        self.decoded_text = widgets.Textarea(layout=widgets.Layout(width='50%'))

        display(self.upload_button, self.edit_button, self.save_button)
        display(widgets.HBox([self.encoded_text, self.decoded_text]))

        if pdf_url:
            self.download_pdf(pdf_url)

    def download_pdf(self, url):
        filename = "/content/final_pdf_with_text (8).pdf"
        os.system(f"wget -O {filename} {url}")
        self.pdf_path = filename
        self.edit_button.disabled = False

    def load_pdf(self, change):
        if self.upload_button.value:
            self.pdf_path = list(self.upload_button.value.keys())[0]
            self.edit_button.disabled = False

    def extract_text(self, event):
        if not self.pdf_path:
            return

        with pdfplumber.open(self.pdf_path) as pdf:
            self.text_blocks = [page.extract_text() or "" for page in pdf.pages]

        full_text = "\n\n".join(self.text_blocks)

        self.encoded_text.value = full_text
        self.decoded_text.value = full_text

        self.save_button.disabled = False

    def save_pdf(self, event):
        if not self.pdf_path:
            return

        new_text = self.encoded_text.value
        new_pdf_path = "kopiy_" + self.pdf_path

        doc = fitz.open()

        for page_text in new_text.split("\n\n"):
            page = doc.new_page()
            page.insert_text((50, 50), page_text, fontsize=12)

        doc.save(new_pdf_path)
        doc.close()

        print(f"Файл сохранён как {new_pdf_path}")

if __name__ == "__main__":
    pdf_url = "/content/final_pdf_with_text (8).pdf"  # Укажите ссылку на ваш PDF
    app = PDFEditor(pdf_url)


FileUpload(value={}, accept='.pdf', description='Upload')

Button(description='Внести правки', disabled=True, style=ButtonStyle())

Button(description='Закончить и сохранить', disabled=True, style=ButtonStyle())

In [13]:
import fitz  # PyMuPDF
import ipywidgets as widgets
from IPython.display import display
import pdfplumber
import os
import chardet

class PDFEditor:
    def __init__(self, pdf_url=None):
        self.pdf_path = ""
        self.text_blocks = []

        self.upload_button = widgets.FileUpload(accept='.pdf', multiple=False)
        self.upload_button.observe(self.load_pdf, names='value')

        self.edit_button = widgets.Button(description="Внести правки", disabled=True)
        self.edit_button.on_click(self.extract_text)

        self.save_button = widgets.Button(description="Закончить и сохранить", disabled=True)
        self.save_button.on_click(self.save_pdf)

        self.encoded_text = widgets.Textarea(layout=widgets.Layout(width='50%', height='500px'))
        self.decoded_text = widgets.Textarea(layout=widgets.Layout(width='50%', height='500px'))

        display(self.upload_button, self.edit_button, self.save_button)
        display(widgets.HBox([self.encoded_text, self.decoded_text]))

        if pdf_url:
            self.download_pdf(pdf_url)

    def download_pdf(self, url):
        filename = "/content/final_pdf_with_text (8).pdf"
        os.system(f"wget -O {filename} {url}")
        self.pdf_path = filename
        self.edit_button.disabled = False

    def load_pdf(self, change):
        if self.upload_button.value:
            self.pdf_path = list(self.upload_button.value.keys())[0]
            self.edit_button.disabled = False

    def extract_text(self, event):
        if not self.pdf_path:
            return

        with pdfplumber.open(self.pdf_path) as pdf:
            raw_text = "\n\n".join([page.to_bytes() for page in pdf.pages if page.to_bytes()])

        detected_encoding = chardet.detect(raw_text)['encoding']
        encoded_text = raw_text.decode(detected_encoding, errors='ignore') if detected_encoding else raw_text

        self.encoded_text.value = raw_text
        self.decoded_text.value = encoded_text

        self.save_button.disabled = False

    def save_pdf(self, event):
        if not self.pdf_path:
            return

        new_text = self.encoded_text.value
        new_pdf_path = "kopiy_" + self.pdf_path

        doc = fitz.open()

        for page_text in new_text.split("\n\n"):
            page = doc.new_page()
            page.insert_text((50, 50), page_text, fontsize=12)

        doc.save(new_pdf_path)
        doc.close()

        print(f"Файл сохранён как {new_pdf_path}")

if __name__ == "__main__":
    pdf_url = "/content/final_pdf_with_text (8).pdf"  # Укажите ссылку на ваш PDF
    app = PDFEditor(pdf_url)


FileUpload(value={}, accept='.pdf', description='Upload')

Button(description='Внести правки', disabled=True, style=ButtonStyle())

Button(description='Закончить и сохранить', disabled=True, style=ButtonStyle())

AttributeError: 'Page' object has no attribute 'to_bytes'

In [18]:
import fitz  # PyMuPDF
import ipywidgets as widgets
from IPython.display import display
import pdfplumber
import os
import chardet

class PDFEditor:
    def __init__(self, pdf_url=None):
        self.pdf_path = ""
        self.text_blocks = []

        self.upload_button = widgets.FileUpload(accept='.pdf', multiple=False)
        self.upload_button.observe(self.load_pdf, names='value')

        self.edit_button = widgets.Button(description="Внести правки", disabled=True)
        self.edit_button.on_click(self.extract_text)

        self.save_button = widgets.Button(description="Закончить и сохранить", disabled=True)
        self.save_button.on_click(self.save_pdf)

        self.encoded_text = widgets.Textarea(layout=widgets.Layout(width='50%', height='500px'))
        self.decoded_text = widgets.Textarea(layout=widgets.Layout(width='50%', height='500px'))

        display(self.upload_button, self.edit_button, self.save_button)
        display(widgets.HBox([self.encoded_text, self.decoded_text]))

        if pdf_url:
            self.download_pdf(pdf_url)

    def download_pdf(self, url):
        filename = "/content/final_pdf_with_text (8).pdf"
        os.system(f"wget -O {filename} {url}")
        self.pdf_path = filename
        self.edit_button.disabled = False

    def load_pdf(self, change):
        if self.upload_button.value:
            self.pdf_path = list(self.upload_button.value.keys())[0]
            self.edit_button.disabled = False

    def extract_text(self, event):
        if not self.pdf_path:
            return

        with pdfplumber.open(self.pdf_path) as pdf:
            raw_text = "\n\n".join([page.extract_text() for page in pdf.pages if page.extract_text()])

        # Определяем кодировку с помощью chardet
        detected_encoding = chardet.detect(raw_text.encode())['encoding']

        # Кодируем текст в байты с найденной кодировкой
        encoded_text = raw_text.encode(detected_encoding)

        # Представляем байты в виде строки с шестнадцатеричными значениями
        encoded_text_str = ' '.join([f'\\x{b:02x}' for b in encoded_text])

        # Декодированный текст (текст в обычной строковой форме)
        decoded_text = raw_text

        # Отображаем закодированный и декодированный текст
        self.encoded_text.value = encoded_text_str
        self.decoded_text.value = decoded_text

        self.save_button.disabled = False

    def save_pdf(self, event):
        if not self.pdf_path:
            return

        new_text = self.encoded_text.value
        new_pdf_path = "kopiy_" + self.pdf_path

        doc = fitz.open()

        for page_text in new_text.split("\n\n"):
            page = doc.new_page()
            page.insert_text((50, 50), page_text, fontsize=12)

        doc.save(new_pdf_path)
        doc.close()

        print(f"Файл сохранён как {new_pdf_path}")

if __name__ == "__main__":
    pdf_url = "/content/final_pdf_with_text (8).pdf"  # Укажите ссылку на ваш PDF
    app = PDFEditor(pdf_url)


FileUpload(value={}, accept='.pdf', description='Upload')

Button(description='Внести правки', disabled=True, style=ButtonStyle())

Button(description='Закончить и сохранить', disabled=True, style=ButtonStyle())

In [19]:
import fitz  # PyMuPDF
import ipywidgets as widgets
from IPython.display import display
import pdfplumber
import os
import chardet

class PDFEditor:
    def __init__(self, pdf_url=None):
        self.pdf_path = ""
        self.text_blocks = []

        self.upload_button = widgets.FileUpload(accept='.pdf', multiple=False)
        self.upload_button.observe(self.load_pdf, names='value')

        self.edit_button = widgets.Button(description="Внести правки", disabled=True)
        self.edit_button.on_click(self.extract_text)

        self.save_button = widgets.Button(description="Закончить и сохранить", disabled=True)
        self.save_button.on_click(self.save_pdf)

        # Создаем виджеты для отображения текста
        self.encoded_text = widgets.Textarea(layout=widgets.Layout(width='50%', height='500px'))
        self.decoded_text = widgets.Textarea(layout=widgets.Layout(width='50%', height='500px'))

        # Добавляем обработчик событий выделения текста
        self.encoded_text.observe(self.highlight_selected_text, names='value')

        display(self.upload_button, self.edit_button, self.save_button)
        display(widgets.HBox([self.encoded_text, self.decoded_text]))

        if pdf_url:
            self.download_pdf(pdf_url)

    def download_pdf(self, url):
        filename = "/content/final_pdf_with_text (8).pdf"
        os.system(f"wget -O {filename} {url}")
        self.pdf_path = filename
        self.edit_button.disabled = False

    def load_pdf(self, change):
        if self.upload_button.value:
            self.pdf_path = list(self.upload_button.value.keys())[0]
            self.edit_button.disabled = False

    def extract_text(self, event):
        if not self.pdf_path:
            return

        with pdfplumber.open(self.pdf_path) as pdf:
            raw_text = "\n\n".join([page.extract_text() for page in pdf.pages if page.extract_text()])

        # Определяем кодировку с помощью chardet
        detected_encoding = chardet.detect(raw_text.encode())['encoding']

        # Кодируем текст в байты с найденной кодировкой
        encoded_text = raw_text.encode(detected_encoding)

        # Представляем байты в виде строки с шестнадцатеричными значениями
        encoded_text_str = ' '.join([f'\\x{b:02x}' for b in encoded_text])

        # Декодированный текст (текст в обычной строковой форме)
        decoded_text = raw_text

        # Отображаем закодированный и декодированный текст
        self.encoded_text.value = encoded_text_str
        self.decoded_text.value = decoded_text

        self.save_button.disabled = False

    def highlight_selected_text(self, change):
        # Получаем выделенный текст из левого окна
        selected_text = change['new']

        # Если есть выделенный текст, подчеркиваем его в правом окне
        if selected_text:
            highlighted_text = self.decoded_text.value.replace(selected_text, f"**{selected_text}**")
        else:
            highlighted_text = self.decoded_text.value

        self.decoded_text.value = highlighted_text

    def save_pdf(self, event):
        if not self.pdf_path:
            return

        new_text = self.encoded_text.value
        new_pdf_path = "kopiy_" + self.pdf_path

        doc = fitz.open()

        for page_text in new_text.split("\n\n"):
            page = doc.new_page()
            page.insert_text((50, 50), page_text, fontsize=12)

        doc.save(new_pdf_path)
        doc.close()

        print(f"Файл сохранён как {new_pdf_path}")

if __name__ == "__main__":
    pdf_url = "/content/final_pdf_with_text (8).pdf"  # Укажите ссылку на ваш PDF
    app = PDFEditor(pdf_url)


FileUpload(value={}, accept='.pdf', description='Upload')

Button(description='Внести правки', disabled=True, style=ButtonStyle())

Button(description='Закончить и сохранить', disabled=True, style=ButtonStyle())

In [21]:
import fitz  # PyMuPDF
import ipywidgets as widgets
from IPython.display import display, Javascript
import pdfplumber
import os
import chardet

class PDFEditor:
    def __init__(self, pdf_url=None):
        self.pdf_path = ""
        self.text_blocks = []

        self.upload_button = widgets.FileUpload(accept='.pdf', multiple=False)
        self.upload_button.observe(self.load_pdf, names='value')

        self.edit_button = widgets.Button(description="Внести правки", disabled=True)
        self.edit_button.on_click(self.extract_text)

        self.save_button = widgets.Button(description="Закончить и сохранить", disabled=True)
        self.save_button.on_click(self.save_pdf)

        # Создаем виджеты для отображения текста
        self.encoded_text = widgets.Textarea(layout=widgets.Layout(width='50%', height='500px'))
        self.decoded_text = widgets.HTML(layout=widgets.Layout(width='50%', height='500px'))

        # Добавляем обработчик событий выделения текста
        self.encoded_text.observe(self.highlight_selected_text, names='value')

        display(self.upload_button, self.edit_button, self.save_button)
        display(widgets.HBox([self.encoded_text, self.decoded_text]))

        if pdf_url:
            self.download_pdf(pdf_url)

    def download_pdf(self, url):
        filename = "/content/final_pdf_with_text (8).pdf"
        os.system(f"wget -O {filename} {url}")
        self.pdf_path = filename
        self.edit_button.disabled = False

    def load_pdf(self, change):
        if self.upload_button.value:
            self.pdf_path = list(self.upload_button.value.keys())[0]
            self.edit_button.disabled = False

    def extract_text(self, event):
        if not self.pdf_path:
            return

        with pdfplumber.open(self.pdf_path) as pdf:
            raw_text = "\n\n".join([page.extract_text() for page in pdf.pages if page.extract_text()])

        # Определяем кодировку с помощью chardet
        detected_encoding = chardet.detect(raw_text.encode())['encoding']

        # Кодируем текст в байты с найденной кодировкой
        encoded_text = raw_text.encode(detected_encoding)

        # Представляем байты в виде строки с шестнадцатеричными значениями
        encoded_text_str = ' '.join([f'\\x{b:02x}' for b in encoded_text])

        # Декодированный текст (текст в обычной строковой форме)
        decoded_text = raw_text

        # Отображаем закодированный и декодированный текст
        self.encoded_text.value = encoded_text_str
        self.decoded_text.value = decoded_text

        self.save_button.disabled = False

    def highlight_selected_text(self, change):
        # Запускаем JavaScript, чтобы получить выделенный текст
        display(Javascript("""
            var selectedText = window.getSelection().toString();
            if (selectedText) {
                // Передаем выделенный текст обратно в Python
                var kernel = Jupyter.notebook.kernel;
                kernel.execute("highlighted_text = '" + selectedText + "'");
            }
        """))

    def highlight_text_in_html(self, text, selected_text):
        # Подсвечиваем выделенное слово жёлтым цветом в HTML
        highlighted = f'<span style="background-color: yellow;">{selected_text}</span>'
        # Заменяем все вхождения выделенного текста на подсвеченную версию
        return text.replace(selected_text, highlighted)

    def save_pdf(self, event):
        if not self.pdf_path:
            return

        new_text = self.encoded_text.value
        new_pdf_path = "kopiy_" + self.pdf_path

        doc = fitz.open()

        for page_text in new_text.split("\n\n"):
            page = doc.new_page()
            page.insert_text((50, 50), page_text, fontsize=12)

        doc.save(new_pdf_path)
        doc.close()

        print(f"Файл сохранён как {new_pdf_path}")

if __name__ == "__main__":
    pdf_url = "/content/final_pdf_with_text (8).pdf"  # Укажите ссылку на ваш PDF
    app = PDFEditor(pdf_url)


FileUpload(value={}, accept='.pdf', description='Upload')

Button(description='Внести правки', disabled=True, style=ButtonStyle())

Button(description='Закончить и сохранить', disabled=True, style=ButtonStyle())

<IPython.core.display.Javascript object>

In [22]:
import fitz  # PyMuPDF
import ipywidgets as widgets
from IPython.display import display
import pdfplumber
import os
import chardet
import time

class PDFEditor:
    def __init__(self, pdf_url=None):
        self.pdf_path = ""
        self.text_blocks = []
        self.selected_text = ""  # Добавляем переменную для хранения выделенного текста

        self.upload_button = widgets.FileUpload(accept='.pdf', multiple=False)
        self.upload_button.observe(self.load_pdf, names='value')

        self.edit_button = widgets.Button(description="Внести правки", disabled=True)
        self.edit_button.on_click(self.extract_text)

        self.save_button = widgets.Button(description="Закончить и сохранить", disabled=True)
        self.save_button.on_click(self.save_pdf)

        # Виджеты для отображения текста
        self.encoded_text = widgets.Textarea(layout=widgets.Layout(width='50%', height='500px'))
        self.decoded_text = widgets.HTML(layout=widgets.Layout(width='50%', height='500px'))

        # Добавляем обработчик выделения
        self.encoded_text.observe(self.track_selected_text, names='value')

        display(self.upload_button, self.edit_button, self.save_button)
        display(widgets.HBox([self.encoded_text, self.decoded_text]))

        if pdf_url:
            self.download_pdf(pdf_url)

    def download_pdf(self, url):
        filename = "/content/final_pdf_with_text (8).pdf"
        os.system(f"wget -O {filename} {url}")
        self.pdf_path = filename
        self.edit_button.disabled = False

    def load_pdf(self, change):
        if self.upload_button.value:
            self.pdf_path = list(self.upload_button.value.keys())[0]
            self.edit_button.disabled = False

    def extract_text(self, event):
        if not self.pdf_path:
            return

        with pdfplumber.open(self.pdf_path) as pdf:
            raw_text = "\n\n".join([page.extract_text() for page in pdf.pages if page.extract_text()])

        # Определяем кодировку с помощью chardet
        detected_encoding = chardet.detect(raw_text.encode())['encoding']

        # Кодируем текст в байты с найденной кодировкой
        encoded_text = raw_text.encode(detected_encoding)

        # Представляем байты в виде строки с шестнадцатеричными значениями
        encoded_text_str = ' '.join([f'\\x{b:02x}' for b in encoded_text])

        # Декодированный текст (текст в обычной строковой форме)
        decoded_text = raw_text

        # Отображаем закодированный и декодированный текст
        self.encoded_text.value = encoded_text_str
        self.decoded_text.value = decoded_text

        self.save_button.disabled = False

    def track_selected_text(self, change):
        """Этот метод будет обновлять выбранный текст при каждом изменении в левом окне"""
        # Получаем выделенный текст из левого окна
        selected = self.encoded_text.value
        if selected:
            self.selected_text = selected

        # Обновляем правое окно подсветкой выделенного текста
        self.update_highlighted_text()

    def update_highlighted_text(self):
        """Обновляем правое окно с подсветкой выделенного текста"""
        highlighted_text = self.highlight_text_in_html(self.encoded_text.value, self.selected_text)
        self.decoded_text.value = highlighted_text

    def highlight_text_in_html(self, text, selected_text):
        """Функция для подсветки выделенного текста"""
        if selected_text:
            highlighted = f'<span style="background-color: yellow;">{selected_text}</span>'
            return text.replace(selected_text, highlighted)
        return text

    def save_pdf(self, event):
        if not self.pdf_path:
            return

        new_text = self.encoded_text.value
        new_pdf_path = "kopiy_" + self.pdf_path

        doc = fitz.open()

        for page_text in new_text.split("\n\n"):
            page = doc.new_page()
            page.insert_text((50, 50), page_text, fontsize=12)

        doc.save(new_pdf_path)
        doc.close()

        print(f"Файл сохранён как {new_pdf_path}")

if __name__ == "__main__":
    pdf_url = "/content/final_pdf_with_text (8).pdf"  # Укажите ссылку на ваш PDF
    app = PDFEditor(pdf_url)


FileUpload(value={}, accept='.pdf', description='Upload')

Button(description='Внести правки', disabled=True, style=ButtonStyle())

Button(description='Закончить и сохранить', disabled=True, style=ButtonStyle())

In [27]:
import fitz  # PyMuPDF
import ipywidgets as widgets
from IPython.display import display
import pdfplumber
import os
import chardet

class PDFEditor:
    def __init__(self, pdf_url=None):
        self.pdf_path = ""
        self.text_blocks = []
        self.selected_text = ""  # Переменная для хранения выделенного текста
        self.raw_text = ""  # Переменная для хранения текста в обычном виде

        self.upload_button = widgets.FileUpload(accept='.pdf', multiple=False)
        self.upload_button.observe(self.load_pdf, names='value')

        self.edit_button = widgets.Button(description="Внести правки", disabled=True)
        self.edit_button.on_click(self.extract_text)

        self.save_button = widgets.Button(description="Закончить и сохранить", disabled=True)
        self.save_button.on_click(self.save_pdf)

        # Виджеты для отображения текста
        self.encoded_text = widgets.Textarea(layout=widgets.Layout(width='50%', height='500px'))
        self.decoded_text = widgets.HTML(layout=widgets.Layout(width='50%', height='500px'))

        # Виджет для поиска текста
        self.search_input = widgets.Text(placeholder="Введите закодированный текст для поиска", layout=widgets.Layout(width='50%'))
        self.search_button = widgets.Button(description="Найти", disabled=False)
        self.search_button.on_click(self.search_and_highlight)

        # Отображаем все виджеты
        display(self.upload_button, self.edit_button, self.save_button)
        display(self.search_input, self.search_button)
        display(widgets.HBox([self.encoded_text, self.decoded_text]))

        if pdf_url:
            self.download_pdf(pdf_url)

    def download_pdf(self, url):
        filename = "/content/final_pdf_with_text (8).pdf"
        os.system(f"wget -O {filename} {url}")
        self.pdf_path = filename
        self.edit_button.disabled = False

    def load_pdf(self, change):
        if self.upload_button.value:
            self.pdf_path = list(self.upload_button.value.keys())[0]
            self.edit_button.disabled = False

    def extract_text(self, event):
        if not self.pdf_path:
            return

        with pdfplumber.open(self.pdf_path) as pdf:
            raw_text = "\n\n".join([page.extract_text() for page in pdf.pages if page.extract_text()])

        # Определяем кодировку с помощью chardet
        detected_encoding = chardet.detect(raw_text.encode())['encoding']

        # Кодируем текст в байты с найденной кодировкой
        encoded_text = raw_text.encode(detected_encoding)

        # Представляем байты в виде строки с шестнадцатеричными значениями
        encoded_text_str = ' '.join([f'\\x{b:02x}' for b in encoded_text])

        # Декодированный текст (текст в обычной строковой форме)
        decoded_text = raw_text

        # Сохраняем в переменные для подсветки
        self.raw_text = raw_text
        self.encoded_text.value = encoded_text_str
        self.decoded_text.value = decoded_text

        self.save_button.disabled = False

    def search_and_highlight(self, event):
        """Этот метод ищет закодированный текст и подсвечивает его в правом окне"""
        search_term = self.search_input.value

        if search_term:
            self.selected_text = search_term
            self.update_highlighted_text()

    def update_highlighted_text(self):
        """Обновляем правое окно с подсветкой выделенного текста"""
        if self.selected_text:
            highlighted_text = self.highlight_text_in_html(self.raw_text, self.selected_text)
            self.decoded_text.value = highlighted_text
        else:
            self.decoded_text.value = self.raw_text

    def highlight_text_in_html(self, text, selected_text):
        """Функция для подсветки выделенного текста"""
        if selected_text:
            highlighted = f'<span style="background-color: yellow;">{selected_text}</span>'
            return text.replace(selected_text, highlighted)
        return text

    def save_pdf(self, event):
        if not self.pdf_path:
            return

        new_text = self.encoded_text.value
        new_pdf_path = "kopiy_" + self.pdf_path

        doc = fitz.open()

        for page_text in new_text.split("\n\n"):
            page = doc.new_page()
            page.insert_text((50, 50), page_text, fontsize=12)

        doc.save(new_pdf_path)
        doc.close()

        print(f"Файл сохранён как {new_pdf_path}")

if __name__ == "__main__":
    pdf_url = "/content/final_pdf_with_text (8).pdf"  # Укажите ссылку на ваш PDF
    app = PDFEditor(pdf_url)


FileUpload(value={}, accept='.pdf', description='Upload')

Button(description='Внести правки', disabled=True, style=ButtonStyle())

Button(description='Закончить и сохранить', disabled=True, style=ButtonStyle())

Text(value='', layout=Layout(width='50%'), placeholder='Введите закодированный текст для поиска')

Button(description='Найти', style=ButtonStyle())

In [32]:
import fitz  # PyMuPDF
import ipywidgets as widgets
from IPython.display import display
import pdfplumber
import os
import chardet

class PDFEditor:
    def __init__(self, pdf_url=None):
        self.pdf_path = ""
        self.text_blocks = []
        self.selected_text = ""  # Переменная для хранения выделенного текста
        self.raw_text = ""  # Переменная для хранения текста в обычном виде
        self.decoded_selected_text = ""  # Переменная для хранения декодированного текста

        self.upload_button = widgets.FileUpload(accept='.pdf', multiple=False)
        self.upload_button.observe(self.load_pdf, names='value')

        self.edit_button = widgets.Button(description="Внести правки", disabled=True)
        self.edit_button.on_click(self.extract_text)

        self.save_button = widgets.Button(description="Закончить и сохранить", disabled=True)
        self.save_button.on_click(self.save_pdf)

        # Виджеты для отображения текста
        self.encoded_text = widgets.Textarea(layout=widgets.Layout(width='50%', height='500px'))
        self.decoded_text = widgets.HTML(layout=widgets.Layout(width='50%', height='500px'))

        # Виджет для поиска текста
        self.search_input = widgets.Text(placeholder="Введите закодированный текст для поиска", layout=widgets.Layout(width='50%'))
        self.search_button = widgets.Button(description="Найти", disabled=False)
        self.search_button.on_click(self.search_and_highlight)

        # Отображаем все виджеты
        display(self.upload_button, self.edit_button, self.save_button)
        display(self.search_input, self.search_button)
        display(widgets.HBox([self.encoded_text, self.decoded_text]))

        if pdf_url:
            self.download_pdf(pdf_url)

    def download_pdf(self, url):
        filename = "/content/final_pdf_with_text (8).pdf"
        os.system(f"wget -O {filename} {url}")
        self.pdf_path = filename
        self.edit_button.disabled = False

    def load_pdf(self, change):
        if self.upload_button.value:
            self.pdf_path = list(self.upload_button.value.keys())[0]
            self.edit_button.disabled = False

    def extract_text(self, event):
        if not self.pdf_path:
            return

        with pdfplumber.open(self.pdf_path) as pdf:
            raw_text = "\n\n".join([page.extract_text() for page in pdf.pages if page.extract_text()])

        # Определяем кодировку с помощью chardet
        detected_encoding = chardet.detect(raw_text.encode())['encoding']

        # Кодируем текст в байты с найденной кодировкой
        encoded_text = raw_text.encode(detected_encoding)

        # Представляем байты в виде строки с шестнадцатеричными значениями
        encoded_text_str = ' '.join([f'\\x{b:02x}' for b in encoded_text])

        # Декодированный текст (текст в обычной строковой форме)
        decoded_text = raw_text

        # Сохраняем в переменные для подсветки
        self.raw_text = raw_text
        self.encoded_text.value = encoded_text_str
        self.decoded_text.value = decoded_text

        self.save_button.disabled = False

    def search_and_highlight(self, event):
        """Этот метод ищет закодированный текст, декодирует его и подсвечивает в правом окне"""
        search_term = self.search_input.value

        if search_term:
            # Декодируем закодированный текст
            decoded_search_term = self.decode_encoded_text(search_term)

            # Сохраняем декодированный текст для подсветки
            self.decoded_selected_text = decoded_search_term
            self.update_highlighted_text()

    def decode_encoded_text(self, encoded_text):
        """Функция для декодирования закодированного текста в нормальный"""
        # Преобразуем строку с шестнадцатеричными значениями в байты
        encoded_bytes = bytes([int(b, 16) for b in encoded_text.split("\\x")[1:] if b])
        decoded_text = encoded_bytes.decode('utf-8', errors='ignore')  # Декодируем байты в текст
        return decoded_text

    def update_highlighted_text(self):
        """Обновляем правое окно с подсветкой декодированного текста"""
        if self.decoded_selected_text:
            highlighted_text = self.highlight_text_in_html(self.raw_text, self.decoded_selected_text)
            self.decoded_text.value = highlighted_text
        else:
            self.decoded_text.value = self.raw_text

    def highlight_text_in_html(self, text, selected_text):
        """Функция для подсветки декодированного текста"""
        if selected_text:
            highlighted = f'<span style="background-color: yellow;">{selected_text}</span>'
            return text.replace(selected_text, highlighted)
        return text

    def save_pdf(self, event):
        if not self.pdf_path:
            return

        new_text = self.encoded_text.value
        new_pdf_path = "kopiy_" + self.pdf_path

        doc = fitz.open()

        for page_text in new_text.split("\n\n"):
            page = doc.new_page()
            page.insert_text((50, 50), page_text, fontsize=12)

        doc.save(new_pdf_path)
        doc.close()

        print(f"Файл сохранён как {new_pdf_path}")

if __name__ == "__main__":
    pdf_url = "/content/COXRANITY"  # Укажите ссылку на ваш PDF
    app = PDFEditor(pdf_url)


FileUpload(value={}, accept='.pdf', description='Upload')

Button(description='Внести правки', disabled=True, style=ButtonStyle())

Button(description='Закончить и сохранить', disabled=True, style=ButtonStyle())

Text(value='', layout=Layout(width='50%'), placeholder='Введите закодированный текст для поиска')

Button(description='Найти', style=ButtonStyle())

IsADirectoryError: [Errno 21] Is a directory: '/content/COXRANITY'

In [33]:
import fitz  # PyMuPDF
import ipywidgets as widgets
from IPython.display import display
import pdfplumber
import os
import chardet

class PDFEditor:
    def __init__(self, pdf_url=None):
        self.pdf_path = ""
        self.text_blocks = []
        self.selected_text = ""  # Переменная для хранения выделенного текста
        self.raw_text = ""  # Переменная для хранения текста в обычном виде
        self.decoded_selected_text = ""  # Переменная для хранения декодированного текста

        self.upload_button = widgets.FileUpload(accept='.pdf', multiple=False)
        self.upload_button.observe(self.load_pdf, names='value')

        self.edit_button = widgets.Button(description="Внести правки", disabled=True)
        self.edit_button.on_click(self.extract_text)

        self.save_button = widgets.Button(description="Закончить и сохранить", disabled=True)
        self.save_button.on_click(self.save_pdf)

        # Виджеты для отображения текста
        self.encoded_text = widgets.Textarea(layout=widgets.Layout(width='50%', height='500px'))
        self.decoded_text = widgets.HTML(layout=widgets.Layout(width='50%', height='500px'))

        # Виджет для поиска текста
        self.search_input = widgets.Text(placeholder="Введите закодированный текст для поиска", layout=widgets.Layout(width='50%'))
        self.search_button = widgets.Button(description="Найти", disabled=False)
        self.search_button.on_click(self.search_and_highlight)

        # Отображаем все виджеты
        display(self.upload_button, self.edit_button, self.save_button)
        display(self.search_input, self.search_button)
        display(widgets.HBox([self.encoded_text, self.decoded_text]))

        if pdf_url:
            self.download_pdf(pdf_url)

    def download_pdf(self, url):
        filename = "/content/final_pdf_with_text (8).pdf"
        os.system(f"wget -O {filename} {url}")
        self.pdf_path = filename
        self.edit_button.disabled = False

    def load_pdf(self, change):
        if self.upload_button.value:
            self.pdf_path = list(self.upload_button.value.keys())[0]
            self.edit_button.disabled = False

    def extract_text(self, event):
        if not self.pdf_path:
            return

        with pdfplumber.open(self.pdf_path) as pdf:
            raw_text = "\n\n".join([page.extract_text() for page in pdf.pages if page.extract_text()])

        # Определяем кодировку с помощью chardet
        detected_encoding = chardet.detect(raw_text.encode())['encoding']

        # Кодируем текст в байты с найденной кодировкой
        encoded_text = raw_text.encode(detected_encoding)

        # Представляем байты в виде строки с шестнадцатеричными значениями
        encoded_text_str = ' '.join([f'\\x{b:02x}' for b in encoded_text])

        # Декодированный текст (текст в обычной строковой форме)
        decoded_text = raw_text

        # Сохраняем в переменные для подсветки
        self.raw_text = raw_text
        self.encoded_text.value = encoded_text_str
        self.decoded_text.value = decoded_text

        self.save_button.disabled = False

    def search_and_highlight(self, event):
        """Этот метод ищет закодированный текст, декодирует его и подсвечивает в правом окне"""
        search_term = self.search_input.value

        if search_term:
            # Декодируем закодированный текст
            decoded_search_term = self.decode_encoded_text(search_term)

            # Сохраняем декодированный текст для подсветки
            self.decoded_selected_text = decoded_search_term
            self.update_highlighted_text()

    def decode_encoded_text(self, encoded_text):
        """Функция для декодирования закодированного текста в нормальный"""
        # Преобразуем строку с шестнадцатеричными значениями в байты
        encoded_bytes = bytes([int(b, 16) for b in encoded_text.split("\\x")[1:] if b])
        decoded_text = encoded_bytes.decode('utf-8', errors='ignore')  # Декодируем байты в текст
        return decoded_text

    def update_highlighted_text(self):
        """Обновляем правое окно с подсветкой декодированного текста"""
        if self.decoded_selected_text:
            highlighted_text = self.highlight_text_in_html(self.raw_text, self.decoded_selected_text)
            self.decoded_text.value = highlighted_text
        else:
            self.decoded_text.value = self.raw_text

    def highlight_text_in_html(self, text, selected_text):
        """Функция для подсветки декодированного текста"""
        if selected_text:
            highlighted = f'<span style="background-color: yellow;">{selected_text}</span>'
            return text.replace(selected_text, highlighted)
        return text

    def save_pdf(self, event):
        if not self.pdf_path:
            return

        new_text = self.encoded_text.value
        new_pdf_path = f"kopiy_{os.path.basename(self.pdf_path)}"  # Генерация корректного пути для сохранения

        doc = fitz.open()

        # Разбиение текста на страницы и добавление текста
        for page_text in new_text.split("\n\n"):
            page = doc.new_page()
            page.insert_text((50, 50), page_text, fontsize=12)

        doc.save(new_pdf_path)  # Сохраняем PDF в новый файл
        doc.close()

        print(f"Файл сохранён как {new_pdf_path}")

if __name__ == "__main__":
    pdf_url = "/content/final_pdf_with_text (8).pdf"  # Укажите ссылку на ваш PDF
    app = PDFEditor(pdf_url)


FileUpload(value={}, accept='.pdf', description='Upload')

Button(description='Внести правки', disabled=True, style=ButtonStyle())

Button(description='Закончить и сохранить', disabled=True, style=ButtonStyle())

Text(value='', layout=Layout(width='50%'), placeholder='Введите закодированный текст для поиска')

Button(description='Найти', style=ButtonStyle())

Файл сохранён как kopiy_final_pdf_with_text (8).pdf


In [35]:
import fitz  # PyMuPDF
import ipywidgets as widgets
from IPython.display import display
import pdfplumber
import os
import chardet

class PDFEditor:
    def __init__(self, pdf_url=None):
        self.pdf_path = ""
        self.text_blocks = []
        self.selected_text = ""  # Переменная для хранения выделенного текста
        self.raw_text = ""  # Переменная для хранения текста в обычном виде
        self.decoded_selected_text = ""  # Переменная для хранения декодированного текста

        self.upload_button = widgets.FileUpload(accept='.pdf', multiple=False)
        self.upload_button.observe(self.load_pdf, names='value')

        self.edit_button = widgets.Button(description="Внести правки", disabled=True)
        self.edit_button.on_click(self.extract_text)

        self.save_button = widgets.Button(description="Закончить и сохранить", disabled=True)
        self.save_button.on_click(self.save_pdf)

        # Виджеты для отображения текста
        self.encoded_text = widgets.Textarea(layout=widgets.Layout(width='50%', height='500px'))
        self.decoded_text = widgets.HTML(layout=widgets.Layout(width='50%', height='500px'))

        # Виджет для поиска текста
        self.search_input = widgets.Text(placeholder="Введите закодированный текст для поиска", layout=widgets.Layout(width='50%'))
        self.search_button = widgets.Button(description="Найти", disabled=False)
        self.search_button.on_click(self.search_and_highlight)

        # Отображаем все виджеты
        display(self.upload_button, self.edit_button, self.save_button)
        display(self.search_input, self.search_button)
        display(widgets.HBox([self.encoded_text, self.decoded_text]))

        if pdf_url:
            self.download_pdf(pdf_url)

    def download_pdf(self, url):
        filename = "/content/final_pdf_with_text (8).pdf"
        os.system(f"wget -O {filename} {url}")
        self.pdf_path = filename
        self.edit_button.disabled = False

    def load_pdf(self, change):
        if self.upload_button.value:
            self.pdf_path = list(self.upload_button.value.keys())[0]
            self.edit_button.disabled = False

    def extract_text(self, event):
        if not self.pdf_path:
            return

        with pdfplumber.open(self.pdf_path) as pdf:
            raw_text = "\n\n".join([page.extract_text() for page in pdf.pages if page.extract_text()])

        # Определяем кодировку с помощью chardet
        detected_encoding = chardet.detect(raw_text.encode())['encoding']

        # Кодируем текст в байты с найденной кодировкой
        encoded_text = raw_text.encode(detected_encoding)

        # Представляем байты в виде строки с шестнадцатеричными значениями
        encoded_text_str = ' '.join([f'\\x{b:02x}' for b in encoded_text])

        # Декодированный текст (текст в обычной строковой форме)
        decoded_text = raw_text

        # Сохраняем в переменные для подсветки
        self.raw_text = raw_text
        self.encoded_text.value = encoded_text_str
        self.decoded_text.value = decoded_text

        self.save_button.disabled = False

    def search_and_highlight(self, event):
        """Этот метод ищет закодированный текст, декодирует его и подсвечивает в правом окне"""
        search_term = self.search_input.value

        if search_term:
            # Декодируем закодированный текст
            decoded_search_term = self.decode_encoded_text(search_term)

            # Сохраняем декодированный текст для подсветки
            self.decoded_selected_text = decoded_search_term
            self.update_highlighted_text()

    def decode_encoded_text(self, encoded_text):
        """Функция для декодирования закодированного текста в нормальный"""
        # Преобразуем строку с шестнадцатеричными значениями в байты
        encoded_bytes = bytes([int(b, 16) for b in encoded_text.split("\\x")[1:] if b])
        decoded_text = encoded_bytes.decode('utf-8', errors='ignore')  # Декодируем байты в текст
        return decoded_text

    def update_highlighted_text(self):
        """Обновляем правое окно с подсветкой декодированного текста"""
        if self.decoded_selected_text:
            highlighted_text = self.highlight_text_in_html(self.raw_text, self.decoded_selected_text)
            self.decoded_text.value = highlighted_text
        else:
            self.decoded_text.value = self.raw_text

    def highlight_text_in_html(self, text, selected_text):
        """Функция для подсветки декодированного текста"""
        if selected_text:
            highlighted = f'<span style="background-color: yellow;">{selected_text}</span>'
            return text.replace(selected_text, highlighted)
        return text

    def save_pdf(self, event):
        if not self.pdf_path:
            return

        # Работаем с оригинальным PDF
        doc = fitz.open(self.pdf_path)  # Загружаем оригинальный файл PDF

        # Пройдем по всем страницам и изменим текст, если он был изменен
        for page_num in range(len(doc)):
            page = doc.load_page(page_num)  # Загружаем страницу
            page_text = page.get_text("text")  # Извлекаем текст с этой страницы

            # Проводим замену текста
            # Для этого нужно иметь оригинальный текст и знать, что заменять
            if self.selected_text:  # Если был выбран текст для замены
                page_text = page_text.replace(self.selected_text, self.decoded_selected_text)

            # Вставляем новый текст (добавляем его на старую позицию)
            page.insert_text((50, 50), page_text, fontsize=12)

        # Сохраняем измененный PDF в новый файл
        new_pdf_path = f"kopiy_{os.path.basename(self.pdf_path)}"
        doc.save(new_pdf_path)
        doc.close()

        print(f"Файл сохранён как {new_pdf_path}")

if __name__ == "__main__":
    pdf_url = "/content/final_pdf_with_text (8).pdf"  # Укажите ссылку на ваш PDF
    app = PDFEditor(pdf_url)


FileUpload(value={}, accept='.pdf', description='Upload')

Button(description='Внести правки', disabled=True, style=ButtonStyle())

Button(description='Закончить и сохранить', disabled=True, style=ButtonStyle())

Text(value='', layout=Layout(width='50%'), placeholder='Введите закодированный текст для поиска')

Button(description='Найти', style=ButtonStyle())

Файл сохранён как kopiy_final_pdf_with_text (8).pdf


In [61]:
import fitz  # PyMuPDF
import ipywidgets as widgets
from IPython.display import display
import pdfplumber
import os
import chardet
import shutil
import tempfile

class PDFEditor:
    def __init__(self, pdf_url=None):
        self.pdf_path = ""
        self.text_blocks = []
        self.selected_text = ""  # Переменная для хранения выделенного текста
        self.raw_text = ""  # Переменная для хранения текста в обычном виде
        self.decoded_selected_text = ""  # Переменная для хранения декодированного текста
        self.temp_pdf_path = None  # Путь к временному PDF

        self.upload_button = widgets.FileUpload(accept='.pdf', multiple=False)
        self.upload_button.observe(self.load_pdf, names='value')

        self.edit_button = widgets.Button(description="Внести правки", disabled=True)
        self.edit_button.on_click(self.extract_text)

        self.save_button = widgets.Button(description="Закончить и сохранить", disabled=True)
        self.save_button.on_click(self.save_pdf)

        # Виджеты для отображения текста
        self.encoded_text = widgets.Textarea(layout=widgets.Layout(width='50%', height='500px'))
        self.decoded_text = widgets.HTML(layout=widgets.Layout(width='50%', height='500px'))

        # Виджет для поиска текста
        self.search_input = widgets.Text(placeholder="Введите закодированный текст для поиска", layout=widgets.Layout(width='50%'))
        self.search_button = widgets.Button(description="Найти", disabled=False)
        self.search_button.on_click(self.search_and_highlight)

        # Отображаем все виджеты
        display(self.upload_button, self.edit_button, self.save_button)
        display(self.search_input, self.search_button)
        display(widgets.HBox([self.encoded_text, self.decoded_text]))

        if pdf_url:
            self.download_pdf(pdf_url)

    def download_pdf(self, url):
        filename = "/content/final_pdf_with_text (8).pdf"
        os.system(f"wget -O {filename} {url}")
        self.pdf_path = filename
        self.edit_button.disabled = False

    def load_pdf(self, change):
        if self.upload_button.value:
            self.pdf_path = list(self.upload_button.value.keys())[0]
            self.edit_button.disabled = False

    def extract_text(self, event):
        if not self.pdf_path:
            return

        with pdfplumber.open(self.pdf_path) as pdf:
            raw_text = "\n\n".join([page.extract_text() for page in pdf.pages if page.extract_text()])

        # Определяем кодировку с помощью chardet
        detected_encoding = chardet.detect(raw_text.encode())['encoding']

        # Кодируем текст в байты с найденной кодировкой
        encoded_text = raw_text.encode(detected_encoding)

        # Представляем байты в виде строки с шестнадцатеричными значениями
        encoded_text_str = ' '.join([f'\\x{b:02x}' for b in encoded_text])

        # Декодированный текст (текст в обычной строковой форме)
        decoded_text = raw_text

        # Сохраняем в переменные для подсветки
        self.raw_text = raw_text
        self.encoded_text.value = encoded_text_str
        self.decoded_text.value = decoded_text

        # Создаем временную копию оригинального PDF
        self.temp_pdf_path = tempfile.mktemp(suffix='.pdf')
        shutil.copy(self.pdf_path, self.temp_pdf_path)

        self.save_button.disabled = False

    def search_and_highlight(self, event):
        """Этот метод ищет закодированный текст, декодирует его и подсвечивает в правом окне"""
        search_term = self.search_input.value

        if search_term:
            # Декодируем закодированный текст
            decoded_search_term = self.decode_encoded_text(search_term)

            # Сохраняем декодированный текст для подсветки
            self.decoded_selected_text = decoded_search_term
            self.update_highlighted_text()

    def decode_encoded_text(self, encoded_text):
        """Функция для декодирования закодированного текста в нормальный"""
        # Преобразуем строку с шестнадцатеричными значениями в байты
        encoded_bytes = bytes([int(b, 16) for b in encoded_text.split("\\x")[1:] if b])
        decoded_text = encoded_bytes.decode('utf-8', errors='ignore')  # Декодируем байты в текст
        return decoded_text

    def update_highlighted_text(self):
        """Обновляем правое окно с подсветкой декодированного текста"""
        if self.decoded_selected_text:
            highlighted_text = self.highlight_text_in_html(self.raw_text, self.decoded_selected_text)
            self.decoded_text.value = highlighted_text
        else:
            self.decoded_text.value = self.raw_text

    def highlight_text_in_html(self, text, selected_text):
        """Функция для подсветки декодированного текста"""
        if selected_text:
            highlighted = f'<span style="background-color: yellow;">{selected_text}</span>'
            return text.replace(selected_text, highlighted)
        return text

    def save_pdf(self, event):
        if not self.temp_pdf_path:
            return

        # Работаем с временным PDF
        doc = fitz.open(self.temp_pdf_path)  # Загружаем временный PDF

        # Пройдем по всем страницам и изменим текст, если он был изменен
        for page_num in range(len(doc)):
            page = doc.load_page(page_num)  # Загружаем страницу
            page_text = page.get_text("text")  # Извлекаем текст с этой страницы

            # Проводим замену текста
            if self.selected_text:  # Если был выбран текст для замены
                page_text = page_text.replace(self.selected_text, self.decoded_selected_text)

            # Вставляем новый текст (добавляем его на старую позицию)
            page.insert_text((50, 50), page_text, fontsize=12)

        # Сохраняем измененный PDF в новый файл
        new_pdf_path = f"kopiy_{os.path.basename(self.pdf_path)}"
        doc.save(new_pdf_path)
        doc.close()

        # Удаляем временный файл
        os.remove(self.temp_pdf_path)

        print(f"Файл сохранён как {new_pdf_path}")

if __name__ == "__main__":
    pdf_url = "/content/final_pdf_with_text (8).pdf"  # Укажите ссылку на ваш PDF
    app = PDFEditor(pdf_url)


FileUpload(value={}, accept='.pdf', description='Upload')

Button(description='Внести правки', disabled=True, style=ButtonStyle())

Button(description='Закончить и сохранить', disabled=True, style=ButtonStyle())

Text(value='', layout=Layout(width='50%'), placeholder='Введите закодированный текст для поиска')

Button(description='Найти', style=ButtonStyle())

Файл сохранён как kopiy_final_pdf_with_text (8).pdf


In [71]:
import fitz  # PyMuPDF
import ipywidgets as widgets
from IPython.display import display
import pdfplumber
import os
import chardet
import shutil
import tempfile

class PDFEditor:
    def __init__(self, pdf_url=None):
        self.pdf_path = ""
        self.text_blocks = []
        self.selected_text = ""  # Переменная для хранения выделенного текста
        self.raw_text = ""  # Переменная для хранения текста в обычном виде
        self.decoded_selected_text = ""  # Переменная для хранения декодированного текста
        self.temp_pdf_path = None  # Путь к временному PDF

        self.upload_button = widgets.FileUpload(accept='.pdf', multiple=False)
        self.upload_button.observe(self.load_pdf, names='value')

        self.edit_button = widgets.Button(description="Внести правки", disabled=True)
        self.edit_button.on_click(self.extract_text)

        self.save_button = widgets.Button(description="Закончить и сохранить", disabled=True)
        self.save_button.on_click(self.save_pdf)

        # Виджеты для отображения текста
        self.encoded_text = widgets.Textarea(layout=widgets.Layout(width='50%', height='500px'))
        self.decoded_text = widgets.HTML(layout=widgets.Layout(width='50%', height='500px'))

        # Виджет для поиска текста
        self.search_input = widgets.Text(placeholder="Введите закодированный текст для поиска", layout=widgets.Layout(width='50%'))
        self.search_button = widgets.Button(description="Найти", disabled=False)
        self.search_button.on_click(self.search_and_highlight)

        # Отображаем все виджеты
        display(self.upload_button, self.edit_button, self.save_button)
        display(self.search_input, self.search_button)
        display(widgets.HBox([self.encoded_text, self.decoded_text]))

        if pdf_url:
            self.download_pdf(pdf_url)

    def download_pdf(self, url):
        filename = "/content/final_pdf_with_text (8).pdf"
        os.system(f"wget -O {filename} {url}")
        self.pdf_path = filename
        self.edit_button.disabled = False

    def load_pdf(self, change):
        if self.upload_button.value:
            self.pdf_path = list(self.upload_button.value.keys())[0]
            self.edit_button.disabled = False

    def extract_text(self, event):
        if not self.pdf_path:
            return

        with pdfplumber.open(self.pdf_path) as pdf:
            raw_text = "\n\n".join([page.extract_text() for page in pdf.pages if page.extract_text()])

        # Определяем кодировку с помощью chardet
        detected_encoding = chardet.detect(raw_text.encode())['encoding']

        # Кодируем текст в байты с найденной кодировкой
        encoded_text = raw_text.encode(detected_encoding)

        # Представляем байты в виде строки с шестнадцатеричными значениями
        encoded_text_str = ' '.join([f'\\x{b:02x}' for b in encoded_text])

        # Декодированный текст (текст в обычной строковой форме)
        decoded_text = raw_text

        # Сохраняем в переменные для подсветки
        self.raw_text = raw_text
        self.encoded_text.value = encoded_text_str
        self.decoded_text.value = decoded_text

        # Создаем временную копию оригинального PDF
        self.temp_pdf_path = tempfile.mktemp(suffix='.pdf')
        shutil.copy(self.pdf_path, self.temp_pdf_path)

        self.save_button.disabled = False

    def search_and_highlight(self, event):
        """Этот метод ищет закодированный текст, декодирует его и подсвечивает в правом окне"""
        search_term = self.search_input.value

        if search_term:
            # Декодируем закодированный текст
            decoded_search_term = self.decode_encoded_text(search_term)

            # Сохраняем декодированный текст для подсветки
            self.decoded_selected_text = decoded_search_term
            self.update_highlighted_text()

    def decode_encoded_text(self, encoded_text):
        """Функция для декодирования закодированного текста в нормальный"""
        # Преобразуем строку с шестнадцатеричными значениями в байты
        encoded_bytes = bytes([int(b, 16) for b in encoded_text.split("\\x")[1:] if b])
        decoded_text = encoded_bytes.decode('utf-8', errors='ignore')  # Декодируем байты в текст
        return decoded_text

    def update_highlighted_text(self):
        """Обновляем правое окно с подсветкой декодированного текста"""
        if self.decoded_selected_text:
            highlighted_text = self.highlight_text_in_html(self.raw_text, self.decoded_selected_text)
            self.decoded_text.value = highlighted_text
        else:
            self.decoded_text.value = self.raw_text

    def highlight_text_in_html(self, text, selected_text):
        """Функция для подсветки декодированного текста"""
        if selected_text:
            highlighted = f'<span style="background-color: yellow;">{selected_text}</span>'
            return text.replace(selected_text, highlighted)
        return text

    def save_pdf(self, event):
        if not self.temp_pdf_path:
            return

        # Работаем с временным PDF
        doc = fitz.open(self.temp_pdf_path)  # Загружаем временный PDF

        # Пройдем по всем страницам и изменим текст, если он был изменен
        for page_num in range(len(doc)):
            page = doc.load_page(page_num)  # Загружаем страницу
            page_text = page.get_text("text")  # Извлекаем текст с этой страницы

            # Проводим замену текста
            if self.selected_text:  # Если был выбран текст для замены
                page_text = page_text.replace(self.selected_text, self.decoded_selected_text)

            # Вставляем новый текст (добавляем его на старую позицию)
            page.insert_text((50, 50), page_text, fontsize=12)

        # Сохраняем измененный PDF в новый файл
        new_pdf_path = f"kopiy_{os.path.basename(self.pdf_path)}"
        doc.save(new_pdf_path)
        doc.close()

        # Удаляем временный файл
        os.remove(self.temp_pdf_path)

        print(f"Файл сохранён как {new_pdf_path}")

if __name__ == "__main__":
    pdf_url = "/content/final_pdf_with_text (8).pdf"  # Укажите ссылку на ваш PDF
    app = PDFEditor(pdf_url)


FileUpload(value={}, accept='.pdf', description='Upload')

Button(description='Внести правки', disabled=True, style=ButtonStyle())

Button(description='Закончить и сохранить', disabled=True, style=ButtonStyle())

Text(value='', layout=Layout(width='50%'), placeholder='Введите закодированный текст для поиска')

Button(description='Найти', style=ButtonStyle())

Файл сохранён как kopiy_final_pdf_with_text (8).pdf


In [73]:
import fitz  # PyMuPDF
import ipywidgets as widgets
from IPython.display import display
import pdfplumber
import os
import chardet
import shutil
import tempfile

class PDFEditor:
    def __init__(self, pdf_url=None):
        self.pdf_path = ""
        self.text_blocks = []
        self.selected_text = ""
        self.raw_text = ""
        self.decoded_selected_text = ""
        self.temp_pdf_path = None

        self.upload_button = widgets.FileUpload(accept='.pdf', multiple=False)
        self.upload_button.observe(self.load_pdf, names='value')

        self.edit_button = widgets.Button(description="Внести правки", disabled=True)
        self.edit_button.on_click(self.extract_text)

        self.save_button = widgets.Button(description="Закончить и сохранить", disabled=True)
        self.save_button.on_click(self.save_pdf)

        # Text widgets
        self.encoded_text = widgets.Textarea(layout=widgets.Layout(width='50%', height='500px'))
        self.decoded_text = widgets.HTML(layout=widgets.Layout(width='50%', height='500px'))

        # Search widget
        self.search_input = widgets.Text(placeholder="Введите закодированный текст для поиска", layout=widgets.Layout(width='50%'))
        self.search_button = widgets.Button(description="Найти", disabled=False)
        self.search_button.on_click(self.search_and_highlight)

        # Display widgets
        display(self.upload_button, self.edit_button, self.save_button)
        display(self.search_input, self.search_button)
        display(widgets.HBox([self.encoded_text, self.decoded_text]))

        if pdf_url:
            self.download_pdf(pdf_url)

    def download_pdf(self, url):
        filename = "/content/final_pdf_with_text (8).pdf"
        os.system(f"wget -O {filename} {url}")
        self.pdf_path = filename
        self.edit_button.disabled = False

    def load_pdf(self, change):
        if self.upload_button.value:
            self.pdf_path = list(self.upload_button.value.keys())[0]
            self.edit_button.disabled = False

    def extract_text(self, event):
        if not self.pdf_path:
            return

        with pdfplumber.open(self.pdf_path) as pdf:
            raw_text = "\n\n".join([page.extract_text() for page in pdf.pages if page.extract_text()])

        detected_encoding = chardet.detect(raw_text.encode())['encoding']
        encoded_text = raw_text.encode(detected_encoding)
        encoded_text_str = ' '.join([f'\\x{b:02x}' for b in encoded_text])

        decoded_text = raw_text

        self.raw_text = raw_text
        self.encoded_text.value = encoded_text_str
        self.decoded_text.value = decoded_text

        self.temp_pdf_path = tempfile.mktemp(suffix='.pdf')
        shutil.copy(self.pdf_path, self.temp_pdf_path)

        self.save_button.disabled = False

    def search_and_highlight(self, event):
        search_term = self.search_input.value

        if search_term:
            decoded_search_term = self.decode_encoded_text(search_term)
            self.decoded_selected_text = decoded_search_term
            self.update_highlighted_text()

    def decode_encoded_text(self, encoded_text):
        encoded_bytes = bytes([int(b, 16) for b in encoded_text.split("\\x")[1:] if b])
        decoded_text = encoded_bytes.decode('utf-8', errors='ignore')
        return decoded_text

    def update_highlighted_text(self):
        if self.decoded_selected_text:
            highlighted_text = self.highlight_text_in_html(self.raw_text, self.decoded_selected_text)
            self.decoded_text.value = highlighted_text
        else:
            self.decoded_text.value = self.raw_text

    def highlight_text_in_html(self, text, selected_text):
        if selected_text:
            highlighted = f'<span style="background-color: yellow;">{selected_text}</span>'
            return text.replace(selected_text, highlighted)
        return text

    def save_pdf(self, event):
        if not self.temp_pdf_path:
            return

        doc = fitz.open(self.temp_pdf_path)

        for page_num in range(len(doc)):
            page = doc.load_page(page_num)
            page_text = page.get_text("text")

            if self.encoded_text.value:
                new_text = self.decode_encoded_text(self.encoded_text.value)
                if page_text != new_text:
                    page.clean_contents()  # Clear existing content
                    page.insert_text((50, 50), new_text, fontsize=12)

        new_pdf_path = f"kopiy_{os.path.basename(self.pdf_path)}"
        doc.save(new_pdf_path)
        doc.close()

        os.remove(self.temp_pdf_path)

        print(f"Файл сохранён как {new_pdf_path}")

if __name__ == "__main__":
    pdf_url = "/content/final_pdf_with_text (8).pdf"
    app = PDFEditor(pdf_url)


FileUpload(value={}, accept='.pdf', description='Upload')

Button(description='Внести правки', disabled=True, style=ButtonStyle())

Button(description='Закончить и сохранить', disabled=True, style=ButtonStyle())

Text(value='', layout=Layout(width='50%'), placeholder='Введите закодированный текст для поиска')

Button(description='Найти', style=ButtonStyle())

Файл сохранён как kopiy_final_pdf_with_text (8).pdf


In [89]:
import fitz  # PyMuPDF
import ipywidgets as widgets
from IPython.display import display
import pdfplumber
import os
import chardet
import shutil
import tempfile

class PDFEditor:
    def __init__(self, pdf_url=None):
        self.pdf_path = ""
        self.text_blocks = []
        self.selected_text = ""
        self.raw_text = ""
        self.decoded_selected_text = ""
        self.temp_pdf_path = None

        # Загрузка PDF
        self.upload_button = widgets.FileUpload(accept='.pdf', multiple=False)
        self.upload_button.observe(self.load_pdf, names='value')

        # Кнопки
        self.edit_button = widgets.Button(description="Внести правки", disabled=True)
        self.edit_button.on_click(self.extract_text)

        self.save_button = widgets.Button(description="Сохранить изменения", disabled=True)
        self.save_button.on_click(self.save_pdf)

        self.refresh_button = widgets.Button(description="Обновить", disabled=False)
        self.refresh_button.on_click(self.refresh_text)

        # Текстовые поля
        self.encoded_text = widgets.Textarea(layout=widgets.Layout(width='50%', height='500px'))
        self.decoded_text = widgets.HTML(layout=widgets.Layout(width='50%', height='500px'))

        # Поиск
        self.search_input = widgets.Text(placeholder="Введите закодированный текст для поиска", layout=widgets.Layout(width='50%'))
        self.search_button = widgets.Button(description="Найти", disabled=False)
        self.search_button.on_click(self.search_and_highlight)

        # Отображение
        display(self.upload_button, self.edit_button, self.save_button, self.refresh_button)
        display(self.search_input, self.search_button)
        display(widgets.HBox([self.encoded_text, self.decoded_text]))

        if pdf_url:
            self.download_pdf(pdf_url)

    def download_pdf(self, url):
        filename = "/content/final_pdf_with_text (8).pdf"
        os.system(f"wget -O {filename} {url}")
        self.pdf_path = filename
        self.edit_button.disabled = False

    def load_pdf(self, change):
        if self.upload_button.value:
            self.pdf_path = list(self.upload_button.value.keys())[0]
            self.edit_button.disabled = False

    def extract_text(self, event):
        if not self.pdf_path:
            return

        with pdfplumber.open(self.pdf_path) as pdf:
            raw_text = "\n\n".join([page.extract_text() for page in pdf.pages if page.extract_text()])

        detected_encoding = chardet.detect(raw_text.encode())['encoding']
        encoded_text = raw_text.encode(detected_encoding)
        encoded_text_str = ' '.join([f'\\x{b:02x}' for b in encoded_text])

        decoded_text = raw_text

        self.raw_text = raw_text
        self.encoded_text.value = encoded_text_str
        self.decoded_text.value = decoded_text

        self.temp_pdf_path = tempfile.mktemp(suffix='.pdf')
        shutil.copy(self.pdf_path, self.temp_pdf_path)

        self.save_button.disabled = False

    def search_and_highlight(self, event):
        search_term = self.search_input.value

        if search_term:
            decoded_search_term = self.decode_encoded_text(search_term)
            self.decoded_selected_text = decoded_search_term
            self.update_highlighted_text()

    def decode_encoded_text(self, encoded_text):
        encoded_bytes = bytes([int(b, 16) for b in encoded_text.split("\\x")[1:] if b])
        decoded_text = encoded_bytes.decode('utf-8', errors='ignore')
        return decoded_text

    def update_highlighted_text(self):
        if self.decoded_selected_text:
            highlighted_text = self.highlight_text_in_html(self.raw_text, self.decoded_selected_text)
            self.decoded_text.value = highlighted_text
        else:
            self.decoded_text.value = self.raw_text

    def highlight_text_in_html(self, text, selected_text):
        if selected_text:
            highlighted = f'<span style="background-color: yellow;">{selected_text}</span>'
            return text.replace(selected_text, highlighted)
        return text

    def refresh_text(self, event):
        # Обновление текста в правом окне после изменения в левом
        self.decoded_text.value = self.encoded_text.value

    def save_pdf(self, event):
        if not self.temp_pdf_path:
            return

        doc = fitz.open(self.temp_pdf_path)

        for page_num in range(len(doc)):
            page = doc.load_page(page_num)
            page_text = page.get_text("text")

            if self.encoded_text.value:
                new_text = self.decode_encoded_text(self.encoded_text.value)
                if page_text != new_text:
                    page.clean_contents()  # Очистка старого контента
                    page.insert_text((50, 50), new_text, fontsize=12)

        new_pdf_path = f"kopiy_{os.path.basename(self.pdf_path)}"
        doc.save(new_pdf_path)
        doc.close()

        os.remove(self.temp_pdf_path)

        print(f"Файл сохранён как {new_pdf_path}")

if __name__ == "__main__":
    pdf_url = "/content/final_pdf_with_text (8).pdf"  # Путь к PDF файлу
    app = PDFEditor(pdf_url)


FileUpload(value={}, accept='.pdf', description='Upload')

Button(description='Внести правки', disabled=True, style=ButtonStyle())

Button(description='Сохранить изменения', disabled=True, style=ButtonStyle())

Button(description='Обновить', style=ButtonStyle())

Text(value='', layout=Layout(width='50%'), placeholder='Введите закодированный текст для поиска')

Button(description='Найти', style=ButtonStyle())

Файл сохранён как kopiy_final_pdf_with_text (8).pdf


In [90]:
import fitz  # PyMuPDF
import ipywidgets as widgets
from IPython.display import display
import pdfplumber
import os
import chardet
import shutil
import tempfile

class PDFEditor:
    def __init__(self, pdf_url=None):
        self.pdf_path = ""
        self.text_blocks = []
        self.text_coords = []  # Список координат для текста
        self.raw_text = ""
        self.decoded_selected_text = ""
        self.temp_pdf_path = None

        # Загрузка PDF
        self.upload_button = widgets.FileUpload(accept='.pdf', multiple=False)
        self.upload_button.observe(self.load_pdf, names='value')

        # Кнопки
        self.edit_button = widgets.Button(description="Внести правки", disabled=True)
        self.edit_button.on_click(self.extract_text)

        self.save_button = widgets.Button(description="Сохранить изменения", disabled=True)
        self.save_button.on_click(self.save_pdf)

        self.refresh_button = widgets.Button(description="Обновить", disabled=False)
        self.refresh_button.on_click(self.refresh_text)

        # Текстовые поля
        self.encoded_text = widgets.Textarea(layout=widgets.Layout(width='50%', height='500px'))
        self.decoded_text = widgets.HTML(layout=widgets.Layout(width='50%', height='500px'))

        # Поиск
        self.search_input = widgets.Text(placeholder="Введите закодированный текст для поиска", layout=widgets.Layout(width='50%'))
        self.search_button = widgets.Button(description="Найти", disabled=False)
        self.search_button.on_click(self.search_and_highlight)

        # Отображение
        display(self.upload_button, self.edit_button, self.save_button, self.refresh_button)
        display(self.search_input, self.search_button)
        display(widgets.HBox([self.encoded_text, self.decoded_text]))

        if pdf_url:
            self.download_pdf(pdf_url)

    def download_pdf(self, url):
        filename = "/content/final_pdf_with_text (8).pdf"
        os.system(f"wget -O {filename} {url}")
        self.pdf_path = filename
        self.edit_button.disabled = False

    def load_pdf(self, change):
        if self.upload_button.value:
            self.pdf_path = list(self.upload_button.value.keys())[0]
            self.edit_button.disabled = False

    def extract_text(self, event):
        if not self.pdf_path:
            return

        with pdfplumber.open(self.pdf_path) as pdf:
            raw_text = "\n\n".join([page.extract_text() for page in pdf.pages if page.extract_text()])

        detected_encoding = chardet.detect(raw_text.encode())['encoding']
        encoded_text = raw_text.encode(detected_encoding)
        encoded_text_str = ' '.join([f'\\x{b:02x}' for b in encoded_text])

        decoded_text = raw_text

        self.raw_text = raw_text
        self.encoded_text.value = encoded_text_str
        self.decoded_text.value = decoded_text

        self.temp_pdf_path = tempfile.mktemp(suffix='.pdf')
        shutil.copy(self.pdf_path, self.temp_pdf_path)

        # Запоминаем координаты текста
        self.extract_text_coordinates()

        self.save_button.disabled = False

    def extract_text_coordinates(self):
        doc = fitz.open(self.temp_pdf_path)

        for page_num in range(len(doc)):
            page = doc.load_page(page_num)
            text_instances = page.search_for(self.raw_text)

            for inst in text_instances:
                # Сохраняем координаты каждой найденной строки
                self.text_coords.append(inst)

        doc.close()

    def search_and_highlight(self, event):
        search_term = self.search_input.value

        if search_term:
            decoded_search_term = self.decode_encoded_text(search_term)
            self.decoded_selected_text = decoded_search_term
            self.update_highlighted_text()

    def decode_encoded_text(self, encoded_text):
        encoded_bytes = bytes([int(b, 16) for b in encoded_text.split("\\x")[1:] if b])
        decoded_text = encoded_bytes.decode('utf-8', errors='ignore')
        return decoded_text

    def update_highlighted_text(self):
        if self.decoded_selected_text:
            highlighted_text = self.highlight_text_in_html(self.raw_text, self.decoded_selected_text)
            self.decoded_text.value = highlighted_text
        else:
            self.decoded_text.value = self.raw_text

    def highlight_text_in_html(self, text, selected_text):
        if selected_text:
            highlighted = f'<span style="background-color: yellow;">{selected_text}</span>'
            return text.replace(selected_text, highlighted)
        return text

    def refresh_text(self, event):
        # Обновление текста в правом окне после изменения в левом
        self.decoded_text.value = self.encoded_text.value

    def save_pdf(self, event):
        if not self.temp_pdf_path:
            return

        doc = fitz.open(self.temp_pdf_path)

        # Вставляем изменения в те места, где был удалён старый текст
        for page_num in range(len(doc)):
            page = doc.load_page(page_num)

            # Для каждой координаты заменяем текст
            for i, coords in enumerate(self.text_coords):
                new_text = self.decode_encoded_text(self.encoded_text.value)
                page.insert_text(coords[:2], new_text, fontsize=12)

        new_pdf_path = f"kopiy_{os.path.basename(self.pdf_path)}"
        doc.save(new_pdf_path)
        doc.close()

        os.remove(self.temp_pdf_path)

        print(f"Файл сохранён как {new_pdf_path}")

if __name__ == "__main__":
    pdf_url = "/content/final_pdf_with_text (8).pdf"  # Путь к PDF файлу
    app = PDFEditor(pdf_url)


FileUpload(value={}, accept='.pdf', description='Upload')

Button(description='Внести правки', disabled=True, style=ButtonStyle())

Button(description='Сохранить изменения', disabled=True, style=ButtonStyle())

Button(description='Обновить', style=ButtonStyle())

Text(value='', layout=Layout(width='50%'), placeholder='Введите закодированный текст для поиска')

Button(description='Найти', style=ButtonStyle())

Файл сохранён как kopiy_final_pdf_with_text (8).pdf


In [93]:
import fitz  # PyMuPDF
import ipywidgets as widgets
from IPython.display import display
import pdfplumber
import os
import chardet
import shutil
import tempfile

class PDFEditor:
    def __init__(self, pdf_url=None):
        self.pdf_path = ""
        self.text_blocks = []  # Список текстовых блоков с координатами
        self.text_coords = []  # Список координат для текста
        self.raw_text = ""
        self.decoded_selected_text = ""
        self.temp_pdf_path = None

        # Загрузка PDF
        self.upload_button = widgets.FileUpload(accept='.pdf', multiple=False)
        self.upload_button.observe(self.load_pdf, names='value')

        # Кнопки
        self.edit_button = widgets.Button(description="Внести правки", disabled=True)
        self.edit_button.on_click(self.extract_text)

        self.save_button = widgets.Button(description="Сохранить изменения", disabled=True)
        self.save_button.on_click(self.save_pdf)

        self.refresh_button = widgets.Button(description="Обновить", disabled=False)
        self.refresh_button.on_click(self.refresh_text)

        # Текстовые поля
        self.encoded_text = widgets.Textarea(layout=widgets.Layout(width='50%', height='500px'))
        self.decoded_text = widgets.HTML(layout=widgets.Layout(width='50%', height='500px'))

        # Поиск
        self.search_input = widgets.Text(placeholder="Введите закодированный текст для поиска", layout=widgets.Layout(width='50%'))
        self.search_button = widgets.Button(description="Найти", disabled=False)
        self.search_button.on_click(self.search_and_highlight)

        # Отображение
        display(self.upload_button, self.edit_button, self.save_button, self.refresh_button)
        display(self.search_input, self.search_button)
        display(widgets.HBox([self.encoded_text, self.decoded_text]))

        if pdf_url:
            self.download_pdf(pdf_url)

    def download_pdf(self, url):
        filename = "/content/final_pdf_with_text (8).pdf"
        os.system(f"wget -O {filename} {url}")
        self.pdf_path = filename
        self.edit_button.disabled = False

    def load_pdf(self, change):
        if self.upload_button.value:
            self.pdf_path = list(self.upload_button.value.keys())[0]
            self.edit_button.disabled = False

    def extract_text(self, event):
        if not self.pdf_path:
            return

        # Открываем PDF с помощью pdfplumber
        with pdfplumber.open(self.pdf_path) as pdf:
            raw_text = "\n\n".join([page.extract_text() for page in pdf.pages if page.extract_text()])

        # Делаем кодировку текста в формат байтов
        detected_encoding = chardet.detect(raw_text.encode())['encoding']
        encoded_text = raw_text.encode(detected_encoding)
        encoded_text_str = ' '.join([f'\\x{b:02x}' for b in encoded_text])

        decoded_text = raw_text

        # Сохраняем исходный текст и запоминаем координаты
        self.raw_text = raw_text
        self.encoded_text.value = encoded_text_str
        self.decoded_text.value = decoded_text

        # Сохраняем временный файл PDF с удалённым текстом
        self.temp_pdf_path = tempfile.mktemp(suffix='NOtext.pdf')
        self.remove_text_from_pdf()

        # Запоминаем координаты текста
        self.extract_text_coordinates()

        self.save_button.disabled = False

    def extract_text_coordinates(self):
        doc = fitz.open(self.temp_pdf_path)

        for page_num in range(len(doc)):
            page = doc.load_page(page_num)
            text_instances = page.search_for(self.raw_text)

            for inst in text_instances:
                # Сохраняем координаты каждой найденной строки
                self.text_coords.append(inst)

        doc.close()

    def remove_text_from_pdf(self):
        # Открываем исходный файл и удаляем текст
        doc = fitz.open(self.pdf_path)
        new_doc = fitz.open()

        for page_num in range(len(doc)):
            page = doc.load_page(page_num)
            new_page = new_doc.new_page(width=page.rect.width, height=page.rect.height)
            new_page.show_pdf_page(page.rect, doc, page_num)

            # Удаляем весь текст на странице
            page.clean_contents()

        # Сохраняем файл без текста
        new_doc.save(self.temp_pdf_path)
        doc.close()
        new_doc.close()

    def search_and_highlight(self, event):
        search_term = self.search_input.value

        if search_term:
            decoded_search_term = self.decode_encoded_text(search_term)
            self.decoded_selected_text = decoded_search_term
            self.update_highlighted_text()

    def decode_encoded_text(self, encoded_text):
        encoded_bytes = bytes([int(b, 16) for b in encoded_text.split("\\x")[1:] if b])
        decoded_text = encoded_bytes.decode('utf-8', errors='ignore')
        return decoded_text

    def update_highlighted_text(self):
        if self.decoded_selected_text:
            highlighted_text = self.highlight_text_in_html(self.raw_text, self.decoded_selected_text)
            self.decoded_text.value = highlighted_text
        else:
            self.decoded_text.value = self.raw_text

    def highlight_text_in_html(self, text, selected_text):
        if selected_text:
            highlighted = f'<span style="background-color: yellow;">{selected_text}</span>'
            return text.replace(selected_text, highlighted)
        return text

    def refresh_text(self, event):
        # Обновление текста в правом окне после изменения в левом
        self.decoded_text.value = self.encoded_text.value

    def save_pdf(self, event):
        if not self.temp_pdf_path:
            return

        doc = fitz.open(self.temp_pdf_path)

        # Вставляем изменения в те места, где был удалён старый текст
        for page_num in range(len(doc)):
            page = doc.load_page(page_num)

            # Для каждой координаты заменяем текст
            for i, coords in enumerate(self.text_coords):
                new_text = self.decode_encoded_text(self.encoded_text.value)
                page.insert_text(coords[:2], new_text, fontsize=12)

        new_pdf_path = f"kopiy_{os.path.basename(self.pdf_path)}"
        doc.save(new_pdf_path)
        doc.close()

        os.remove(self.temp_pdf_path)

        print(f"Файл сохранён как {new_pdf_path}")

if __name__ == "__main__":
    pdf_url = "/content/final_pdf_with_text (8).pdf"  # Путь к PDF файлу
    app = PDFEditor(pdf_url)


FileUpload(value={}, accept='.pdf', description='Upload')

Button(description='Внести правки', disabled=True, style=ButtonStyle())

Button(description='Сохранить изменения', disabled=True, style=ButtonStyle())

Button(description='Обновить', style=ButtonStyle())

Text(value='', layout=Layout(width='50%'), placeholder='Введите закодированный текст для поиска')

Button(description='Найти', style=ButtonStyle())

Файл сохранён как kopiy_final_pdf_with_text (8).pdf


In [96]:
!apt update
!apt install -y libreoffice
!pip install pdf2docx python-docx

import fitz  # PyMuPDF
import ipywidgets as widgets
from IPython.display import display
import os
import chardet
import shutil
import tempfile
from pdf2docx import Converter
from docx import Document
import uuid

class PDFEditor:
    def __init__(self, pdf_url=None):
        self.pdf_path = ""
        self.text_blocks = []  # Список текстовых блоков с координатами
        self.text_coords = []  # Список координат для текста
        self.raw_text = ""
        self.decoded_selected_text = ""
        self.temp_pdf_path = None
        self.word_file_path = None

        # Загрузка PDF
        self.upload_button = widgets.FileUpload(accept='.pdf', multiple=False)
        self.upload_button.observe(self.load_pdf, names='value')

        # Кнопки
        self.edit_button = widgets.Button(description="Внести правки", disabled=True)
        self.edit_button.on_click(self.extract_text)

        self.save_button = widgets.Button(description="Сохранить изменения", disabled=True)
        self.save_button.on_click(self.save_pdf)

        self.refresh_button = widgets.Button(description="Обновить", disabled=False)
        self.refresh_button.on_click(self.refresh_text)

        # Текстовые поля
        self.encoded_text = widgets.Textarea(layout=widgets.Layout(width='50%', height='500px'))
        self.decoded_text = widgets.HTML(layout=widgets.Layout(width='50%', height='500px'))

        # Поиск
        self.search_input = widgets.Text(placeholder="Введите закодированный текст для поиска", layout=widgets.Layout(width='50%'))
        self.search_button = widgets.Button(description="Найти", disabled=False)
        self.search_button.on_click(self.search_and_highlight)

        # Отображение
        display(self.upload_button, self.edit_button, self.save_button, self.refresh_button)
        display(self.search_input, self.search_button)
        display(widgets.HBox([self.encoded_text, self.decoded_text]))

        if pdf_url:
            self.download_pdf(pdf_url)

    def download_pdf(self, url):
        filename = "/content/final_pdf_with_text (8).pdf"
        os.system(f"wget -O {filename} {url}")
        self.pdf_path = filename
        self.edit_button.disabled = False

    def load_pdf(self, change):
        if self.upload_button.value:
            self.pdf_path = list(self.upload_button.value.keys())[0]
            self.edit_button.disabled = False

    def extract_text(self, event):
        if not self.pdf_path:
            return

        # Конвертируем PDF в Word с сохранением изображений
        self.word_file_path = "/content/converted.docx"
        cv = Converter(self.pdf_path)
        cv.convert(self.word_file_path, start=0, end=None)
        cv.close()

        # Открываем документ Word
        doc = Document(self.word_file_path)
        raw_text = ""
        self.text_coords = []  # Список для хранения координат (будет использован позже)

        for para in doc.paragraphs:
            raw_text += para.text + "\n"

        # Сохраняем исходный текст и отображаем его
        self.raw_text = raw_text
        self.encoded_text.value = self.encode_text(raw_text)
        self.decoded_text.value = raw_text

        # Разрешаем сохранить файл
        self.save_button.disabled = False

    def encode_text(self, text):
        encoded_text = text.encode('utf-8')
        return ' '.join([f'\\x{b:02x}' for b in encoded_text])

    def search_and_highlight(self, event):
        search_term = self.search_input.value

        if search_term:
            decoded_search_term = self.decode_encoded_text(search_term)
            self.decoded_selected_text = decoded_search_term
            self.update_highlighted_text()

    def decode_encoded_text(self, encoded_text):
        encoded_bytes = bytes([int(b, 16) for b in encoded_text.split("\\x")[1:] if b])
        decoded_text = encoded_bytes.decode('utf-8', errors='ignore')
        return decoded_text

    def update_highlighted_text(self):
        if self.decoded_selected_text:
            highlighted_text = self.highlight_text_in_html(self.raw_text, self.decoded_selected_text)
            self.decoded_text.value = highlighted_text
        else:
            self.decoded_text.value = self.raw_text

    def highlight_text_in_html(self, text, selected_text):
        if selected_text:
            highlighted = f'<span style="background-color: yellow;">{selected_text}</span>'
            return text.replace(selected_text, highlighted)
        return text

    def refresh_text(self, event):
        # Обновление текста в правом окне после изменения в левом
        self.decoded_text.value = self.encoded_text.value

    def save_pdf(self, event):
        if not self.word_file_path:
            return

        # Сохраняем изменения обратно в Word
        doc = Document(self.word_file_path)

        # Обновляем текст в документе
        updated_text = self.decode_encoded_text(self.encoded_text.value)
        for para in doc.paragraphs:
            if para.text in self.raw_text:
                para.text = updated_text

        # Сохраняем Word файл
        word_temp_path = f"/content/updated_{uuid.uuid4()}.docx"
        doc.save(word_temp_path)

        # Конвертируем обратно в PDF
        new_pdf_path = f"/content/updated_{uuid.uuid4()}.pdf"
        os.system(f"libreoffice --headless --convert-to pdf {word_temp_path} --outdir /content")

        print(f"Файл сохранён как {new_pdf_path}")

if __name__ == "__main__":
    pdf_url = "/content/final_pdf_with_text (8).pdf"  # Путь к PDF файлу
    app = PDFEditor(pdf_url)


Hit:1 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ InRelease
Hit:2 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  InRelease
Hit:3 http://security.ubuntu.com/ubuntu jammy-security InRelease
Hit:4 http://archive.ubuntu.com/ubuntu jammy InRelease
Hit:5 http://archive.ubuntu.com/ubuntu jammy-updates InRelease
Hit:6 http://archive.ubuntu.com/ubuntu jammy-backports InRelease
Hit:7 https://r2u.stat.illinois.edu/ubuntu jammy InRelease
Hit:8 https://ppa.launchpadcontent.net/deadsnakes/ppa/ubuntu jammy InRelease
Hit:9 https://ppa.launchpadcontent.net/graphics-drivers/ppa/ubuntu jammy InRelease
Hit:10 https://ppa.launchpadcontent.net/ubuntugis/ppa/ubuntu jammy InRelease
Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
32 packages can be upgraded. Run 'apt list --upgradable' to see them.
W: Skipping acquire of configured file 'main/source/Sources' as repository 'https://r2u.stat.illinois.edu/ubuntu jammy InR

FileUpload(value={}, accept='.pdf', description='Upload')

Button(description='Внести правки', disabled=True, style=ButtonStyle())

Button(description='Сохранить изменения', disabled=True, style=ButtonStyle())

Button(description='Обновить', style=ButtonStyle())

Text(value='', layout=Layout(width='50%'), placeholder='Введите закодированный текст для поиска')

Button(description='Найти', style=ButtonStyle())

ERROR:root:Ignore page 2 due to making page error: invalid literal for int() with base 16: 'x1'
ERROR:root:Ignore page 3 due to making page error: invalid literal for int() with base 16: 'x1'
ERROR:root:Ignore page 4 due to making page error: invalid literal for int() with base 16: 'x1'
ERROR:root:Ignore page 5 due to making page error: invalid literal for int() with base 16: 'x1'
ERROR:root:Ignore page 6 due to making page error: invalid literal for int() with base 16: 'x1'
ERROR:root:Ignore page 7 due to making page error: invalid literal for int() with base 16: 'x1'
ERROR:root:Ignore page 8 due to making page error: invalid literal for int() with base 16: 'x1'
ERROR:root:Ignore page 9 due to making page error: invalid literal for int() with base 16: 'x1'
ERROR:root:Ignore page 10 due to making page error: invalid literal for int() with base 16: 'x1'
ERROR:root:Ignore page 11 due to making page error: invalid literal for int() with base 16: 'x1'
ERROR:root:Ignore page 12 due to makin

Файл сохранён как /content/updated_6b121438-3c3a-4273-a4b4-28349f8b9196.pdf


In [102]:
#!apt update
#!apt install -y libreoffice
#!pip install pdf2docx python-docx ipywidgets fitz

import fitz  # PyMuPDF
import ipywidgets as widgets
from IPython.display import display
import os
import uuid
from pdf2docx import Converter
from docx import Document
import shutil

class PDFEditor:
    def __init__(self, pdf_url=None):
        self.pdf_path = ""
        self.text_blocks = []  # Список текстовых блоков с координатами
        self.text_coords = []  # Список координат для текста
        self.raw_text = ""
        self.temp_pdf_path = None
        self.word_file_path = None

        # Загрузка PDF
        self.upload_button = widgets.FileUpload(accept='.pdf', multiple=False)
        self.upload_button.observe(self.load_pdf, names='value')

        # Кнопки
        self.edit_button = widgets.Button(description="Внести правки", disabled=True)
        self.edit_button.on_click(self.extract_text)

        self.save_button = widgets.Button(description="Сохранить изменения", disabled=True)
        self.save_button.on_click(self.save_pdf)

        self.refresh_button = widgets.Button(description="Обновить", disabled=False)
        self.refresh_button.on_click(self.refresh_text)

        # Текстовые поля
        self.encoded_text = widgets.Textarea(layout=widgets.Layout(width='50%', height='500px'))
        self.decoded_text = widgets.HTML(layout=widgets.Layout(width='50%', height='500px'))

        # Поиск
        self.search_input = widgets.Text(placeholder="Введите закодированный текст для поиска", layout=widgets.Layout(width='50%'))
        self.search_button = widgets.Button(description="Найти", disabled=False)
        self.search_button.on_click(self.search_and_highlight)

        # Отображение
        display(self.upload_button, self.edit_button, self.save_button, self.refresh_button)
        display(self.search_input, self.search_button)
        display(widgets.HBox([self.encoded_text, self.decoded_text]))

        if pdf_url:
            self.download_pdf(pdf_url)

    def download_pdf(self, url):
        filename = "/content/final_pdf_with_text (8).pdf"
        os.system(f"wget -O {filename} {url}")
        self.pdf_path = filename
        self.edit_button.disabled = False

    def load_pdf(self, change):
        if self.upload_button.value:
            self.pdf_path = list(self.upload_button.value.keys())[0]
            self.edit_button.disabled = False

    def extract_text(self, event):
        if not self.pdf_path:
            return

        # Извлекаем текст и координаты из оригинального PDF с помощью PyMuPDF
        self.text_blocks = []
        self.text_coords = []
        self.raw_text = ""

        doc = fitz.open(self.pdf_path)

        for page_num in range(len(doc)):
            page = doc.load_page(page_num)
            blocks = page.get_text("dict")["blocks"]
            for block in blocks:
                if block["type"] == 0:  # Это текстовый блок
                    for line in block["lines"]:
                        for span in line["spans"]:
                            text = span["text"]
                            bbox = span["bbox"]  # Координаты блока текста
                            self.text_blocks.append({"text": text, "bbox": bbox})
                            self.raw_text += text + "\n"

        # Отображаем извлечённый текст в кодированном и нормальном виде
        self.encoded_text.value = self.encode_text(self.raw_text)
        self.decoded_text.value = self.raw_text

        # Сохраняем путь к временной копии PDF
        self.temp_pdf_path = "/content/temp_copy.pdf"
        shutil.copy(self.pdf_path, self.temp_pdf_path)

        # Разрешаем сохранить файл
        self.save_button.disabled = False

    def encode_text(self, text):
        encoded_text = text.encode('utf-8')
        return ' '.join([f'\\x{b:02x}' for b in encoded_text])

    def search_and_highlight(self, event):
        search_term = self.search_input.value

        if search_term:
            decoded_search_term = self.decode_encoded_text(search_term)
            self.decoded_selected_text = decoded_search_term
            self.update_highlighted_text()

    def decode_encoded_text(self, encoded_text):
        encoded_bytes = bytes([int(b, 16) for b in encoded_text.split("\\x")[1:] if b])
        decoded_text = encoded_bytes.decode('utf-8', errors='ignore')
        return decoded_text

    def update_highlighted_text(self):
        if self.decoded_selected_text:
            highlighted_text = self.highlight_text_in_html(self.raw_text, self.decoded_selected_text)
            self.decoded_text.value = highlighted_text
        else:
            self.decoded_text.value = self.raw_text

    def highlight_text_in_html(self, text, selected_text):
        if selected_text:
            highlighted = f'<span style="background-color: yellow;">{selected_text}</span>'
            return text.replace(selected_text, highlighted)
        return text

    def refresh_text(self, event):
        # Обновление текста в правом окне после изменения в левом
        self.decoded_text.value = self.encoded_text.value

    def save_pdf(self, event):
        if not self.temp_pdf_path:
            return

        # Сохраняем изменения в Word
        doc = Document()
        doc.add_paragraph(self.decode_encoded_text(self.encoded_text.value))

        word_temp_path = f"/content/updated_{uuid.uuid4()}.docx"
        doc.save(word_temp_path)

        # Конвертируем Word обратно в PDF
        new_pdf_path = f"/content/updated_{uuid.uuid4()}.pdf"
        os.system(f"libreoffice --headless --convert-to pdf {word_temp_path} --outdir /content")

        print(f"Файл сохранён как {new_pdf_path}")

if __name__ == "__main__":
    pdf_url = "/content/final_pdf_with_text (8).pdf"  # Путь к PDF файлу
    app = PDFEditor(pdf_url)


FileUpload(value={}, accept='.pdf', description='Upload')

Button(description='Внести правки', disabled=True, style=ButtonStyle())

Button(description='Сохранить изменения', disabled=True, style=ButtonStyle())

Button(description='Обновить', style=ButtonStyle())

Text(value='', layout=Layout(width='50%'), placeholder='Введите закодированный текст для поиска')

Button(description='Найти', style=ButtonStyle())

Файл сохранён как /content/updated_301bdf9b-b30b-4c4a-b3da-34160cbe74d6.pdf


In [103]:
import fitz  # PyMuPDF
import ipywidgets as widgets
from IPython.display import display
import os
import uuid
from pdf2docx import Converter
from docx import Document
import shutil
from io import BytesIO
from PIL import Image

class PDFEditor:
    def __init__(self, pdf_url=None):
        self.pdf_path = ""
        self.text_blocks = []  # Список текстовых блоков с координатами
        self.text_coords = []  # Список координат для текста
        self.images = []  # Список для хранения изображений и их координат
        self.raw_text = ""
        self.temp_pdf_path = None
        self.word_file_path = None

        # Загрузка PDF
        self.upload_button = widgets.FileUpload(accept='.pdf', multiple=False)
        self.upload_button.observe(self.load_pdf, names='value')

        # Кнопки
        self.edit_button = widgets.Button(description="Внести правки", disabled=True)
        self.edit_button.on_click(self.extract_text)

        self.save_button = widgets.Button(description="Сохранить изменения", disabled=True)
        self.save_button.on_click(self.save_pdf)

        self.refresh_button = widgets.Button(description="Обновить", disabled=False)
        self.refresh_button.on_click(self.refresh_text)

        # Текстовые поля
        self.encoded_text = widgets.Textarea(layout=widgets.Layout(width='50%', height='500px'))
        self.decoded_text = widgets.HTML(layout=widgets.Layout(width='50%', height='500px'))

        # Поиск
        self.search_input = widgets.Text(placeholder="Введите закодированный текст для поиска", layout=widgets.Layout(width='50%'))
        self.search_button = widgets.Button(description="Найти", disabled=False)
        self.search_button.on_click(self.search_and_highlight)

        # Отображение
        display(self.upload_button, self.edit_button, self.save_button, self.refresh_button)
        display(self.search_input, self.search_button)
        display(widgets.HBox([self.encoded_text, self.decoded_text]))

        if pdf_url:
            self.download_pdf(pdf_url)

    def download_pdf(self, url):
        filename = "/content/final_pdf_with_text (8).pdf"
        os.system(f"wget -O {filename} {url}")
        self.pdf_path = filename
        self.edit_button.disabled = False

    def load_pdf(self, change):
        if self.upload_button.value:
            self.pdf_path = list(self.upload_button.value.keys())[0]
            self.edit_button.disabled = False

    def extract_text(self, event):
        if not self.pdf_path:
            return

        # Извлекаем текст и координаты из оригинального PDF с помощью PyMuPDF
        self.text_blocks = []
        self.text_coords = []
        self.images = []
        self.raw_text = ""

        doc = fitz.open(self.pdf_path)

        for page_num in range(len(doc)):
            page = doc.load_page(page_num)
            blocks = page.get_text("dict")["blocks"]
            for block in blocks:
                if block["type"] == 0:  # Это текстовый блок
                    for line in block["lines"]:
                        for span in line["spans"]:
                            text = span["text"]
                            bbox = span["bbox"]  # Координаты блока текста
                            self.text_blocks.append({"text": text, "bbox": bbox})
                            self.raw_text += text + "\n"

            # Извлекаем изображения
            for img_index, img in enumerate(page.get_images(full=True)):
                xref = img[0]
                base_image = doc.extract_image(xref)
                image_bytes = base_image["image"]
                image = Image.open(BytesIO(image_bytes))
                self.images.append({"image": image, "bbox": img[1]})

        # Отображаем извлечённый текст в кодированном и нормальном виде
        self.encoded_text.value = self.encode_text(self.raw_text)
        self.decoded_text.value = self.raw_text

        # Сохраняем путь к временной копии PDF
        self.temp_pdf_path = "/content/temp_copy.pdf"
        shutil.copy(self.pdf_path, self.temp_pdf_path)

        # Разрешаем сохранить файл
        self.save_button.disabled = False

    def encode_text(self, text):
        encoded_text = text.encode('utf-8')
        return ' '.join([f'\\x{b:02x}' for b in encoded_text])

    def search_and_highlight(self, event):
        search_term = self.search_input.value

        if search_term:
            decoded_search_term = self.decode_encoded_text(search_term)
            self.decoded_selected_text = decoded_search_term
            self.update_highlighted_text()

    def decode_encoded_text(self, encoded_text):
        encoded_bytes = bytes([int(b, 16) for b in encoded_text.split("\\x")[1:] if b])
        decoded_text = encoded_bytes.decode('utf-8', errors='ignore')
        return decoded_text

    def update_highlighted_text(self):
        if self.decoded_selected_text:
            highlighted_text = self.highlight_text_in_html(self.raw_text, self.decoded_selected_text)
            self.decoded_text.value = highlighted_text
        else:
            self.decoded_text.value = self.raw_text

    def highlight_text_in_html(self, text, selected_text):
        if selected_text:
            highlighted = f'<span style="background-color: yellow;">{selected_text}</span>'
            return text.replace(selected_text, highlighted)
        return text

    def refresh_text(self, event):
        # Обновление текста в правом окне после изменения в левом
        self.decoded_text.value = self.encoded_text.value

    def save_pdf(self, event):
        if not self.temp_pdf_path:
            return

        # Сохраняем изменения в Word
        doc = Document()
        doc.add_paragraph(self.decode_encoded_text(self.encoded_text.value))

        word_temp_path = f"/content/updated_{uuid.uuid4()}.docx"
        doc.save(word_temp_path)

        # Конвертируем Word обратно в PDF
        new_pdf_path = f"/content/updated_{uuid.uuid4()}.pdf"
        os.system(f"libreoffice --headless --convert-to pdf {word_temp_path} --outdir /content")

        # Вставляем изображения в новый PDF на тех же координатах
        self.insert_images(new_pdf_path)

        print(f"Файл сохранён как {new_pdf_path}")

    def insert_images(self, pdf_path):
        # Открываем новый PDF
        new_doc = fitz.open(pdf_path)

        # Вставляем изображения на соответствующие места
        for i, img_data in enumerate(self.images):
            image = img_data["image"]
            bbox = img_data["bbox"]

            # Вставляем изображение в PDF
            new_page = new_doc.load_page(i)  # загружаем соответствующую страницу
            rect = fitz.Rect(bbox)  # Координаты для вставки изображения
            img_bytes = BytesIO()
            image.save(img_bytes, format="PNG")
            img_bytes.seek(0)

            # Вставляем изображение в указанное место
            new_page.insert_image(rect, stream=img_bytes)

        # Сохраняем новый PDF с изображениями
        new_pdf_path = f"/content/updated_with_images_{uuid.uuid4()}.pdf"
        new_doc.save(new_pdf_path)
        print(f"Изображения вставлены, новый файл: {new_pdf_path}")

if __name__ == "__main__":
    pdf_url = "/content/final_pdf_with_text (8).pdf"  # Путь к PDF файлу
    app = PDFEditor(pdf_url)


FileUpload(value={}, accept='.pdf', description='Upload')

Button(description='Внести правки', disabled=True, style=ButtonStyle())

Button(description='Сохранить изменения', disabled=True, style=ButtonStyle())

Button(description='Обновить', style=ButtonStyle())

Text(value='', layout=Layout(width='50%'), placeholder='Введите закодированный текст для поиска')

Button(description='Найти', style=ButtonStyle())

FileNotFoundError: no such file: '/content/updated_89142179-ddd7-40d2-ae9c-f82a0857c171.pdf'

In [105]:
import fitz  # PyMuPDF
import ipywidgets as widgets
from IPython.display import display
import os
import uuid
from pdf2docx import Converter
from docx import Document
import shutil
from io import BytesIO
from PIL import Image
import time  # Для добавления задержки

class PDFEditor:
    def __init__(self, pdf_url=None):
        self.pdf_path = ""
        self.text_blocks = []  # Список текстовых блоков с координатами
        self.text_coords = []  # Список координат для текста
        self.images = []  # Список для хранения изображений и их координат
        self.raw_text = ""
        self.temp_pdf_path = None
        self.word_file_path = None

        # Загрузка PDF
        self.upload_button = widgets.FileUpload(accept='.pdf', multiple=False)
        self.upload_button.observe(self.load_pdf, names='value')

        # Кнопки
        self.edit_button = widgets.Button(description="Внести правки", disabled=True)
        self.edit_button.on_click(self.extract_text)

        self.save_button = widgets.Button(description="Сохранить изменения", disabled=True)
        self.save_button.on_click(self.save_pdf)

        self.refresh_button = widgets.Button(description="Обновить", disabled=False)
        self.refresh_button.on_click(self.refresh_text)

        # Текстовые поля
        self.encoded_text = widgets.Textarea(layout=widgets.Layout(width='50%', height='500px'))
        self.decoded_text = widgets.HTML(layout=widgets.Layout(width='50%', height='500px'))

        # Поиск
        self.search_input = widgets.Text(placeholder="Введите закодированный текст для поиска", layout=widgets.Layout(width='50%'))
        self.search_button = widgets.Button(description="Найти", disabled=False)
        self.search_button.on_click(self.search_and_highlight)

        # Отображение
        display(self.upload_button, self.edit_button, self.save_button, self.refresh_button)
        display(self.search_input, self.search_button)
        display(widgets.HBox([self.encoded_text, self.decoded_text]))

        if pdf_url:
            self.download_pdf(pdf_url)

    def download_pdf(self, url):
        filename = "/content/final_pdf_with_text (8).pdf"
        os.system(f"wget -O {filename} {url}")
        self.pdf_path = filename
        self.edit_button.disabled = False

    def load_pdf(self, change):
        if self.upload_button.value:
            self.pdf_path = list(self.upload_button.value.keys())[0]
            self.edit_button.disabled = False

    def extract_text(self, event):
        if not self.pdf_path:
            return

        # Извлекаем текст и координаты из оригинального PDF с помощью PyMuPDF
        self.text_blocks = []
        self.text_coords = []
        self.images = []
        self.raw_text = ""

        doc = fitz.open(self.pdf_path)

        for page_num in range(len(doc)):
            page = doc.load_page(page_num)
            blocks = page.get_text("dict")["blocks"]
            for block in blocks:
                if block["type"] == 0:  # Это текстовый блок
                    for line in block["lines"]:
                        for span in line["spans"]:
                            text = span["text"]
                            bbox = span["bbox"]  # Координаты блока текста
                            self.text_blocks.append({"text": text, "bbox": bbox})
                            self.raw_text += text + "\n"

            # Извлекаем изображения
            for img_index, img in enumerate(page.get_images(full=True)):
                xref = img[0]
                base_image = doc.extract_image(xref)
                image_bytes = base_image["image"]
                image = Image.open(BytesIO(image_bytes))
                self.images.append({"image": image, "bbox": img[1]})

        # Отображаем извлечённый текст в кодированном и нормальном виде
        self.encoded_text.value = self.encode_text(self.raw_text)
        self.decoded_text.value = self.raw_text

        # Сохраняем путь к временной копии PDF
        self.temp_pdf_path = "/content/temp_copy.pdf"
        shutil.copy(self.pdf_path, self.temp_pdf_path)

        # Разрешаем сохранить файл
        self.save_button.disabled = False

    def encode_text(self, text):
        encoded_text = text.encode('utf-8')
        return ' '.join([f'\\x{b:02x}' for b in encoded_text])

    def search_and_highlight(self, event):
        search_term = self.search_input.value

        if search_term:
            decoded_search_term = self.decode_encoded_text(search_term)
            self.decoded_selected_text = decoded_search_term
            self.update_highlighted_text()

    def decode_encoded_text(self, encoded_text):
        encoded_bytes = bytes([int(b, 16) for b in encoded_text.split("\\x")[1:] if b])
        decoded_text = encoded_bytes.decode('utf-8', errors='ignore')
        return decoded_text

    def update_highlighted_text(self):
        if self.decoded_selected_text:
            highlighted_text = self.highlight_text_in_html(self.raw_text, self.decoded_selected_text)
            self.decoded_text.value = highlighted_text
        else:
            self.decoded_text.value = self.raw_text

    def highlight_text_in_html(self, text, selected_text):
        if selected_text:
            highlighted = f'<span style="background-color: yellow;">{selected_text}</span>'
            return text.replace(selected_text, highlighted)
        return text

    def refresh_text(self, event):
        # Обновление текста в правом окне после изменения в левом
        self.decoded_text.value = self.encoded_text.value

    def save_pdf(self, event):
        if not self.temp_pdf_path:
            return

        # Сохраняем изменения в Word
        doc = Document()
        doc.add_paragraph(self.decode_encoded_text(self.encoded_text.value))

        word_temp_path = f"/content/updated_{uuid.uuid4()}.docx"
        doc.save(word_temp_path)

        # Конвертируем Word обратно в PDF
        new_pdf_path = f"/content/updated_{uuid.uuid4()}.pdf"
        os.system(f"libreoffice --headless --convert-to pdf {word_temp_path} --outdir /content")

        # Вставляем изображения в новый PDF на тех же координатах с задержкой
        self.insert_images(new_pdf_path)

        print(f"Файл сохранён как {new_pdf_path}")

    def insert_images(self, pdf_path):
        # Открываем новый PDF
        new_doc = fitz.open(pdf_path)

        # Вставляем изображения на соответствующие места с задержкой
        for i, img_data in enumerate(self.images):
            image = img_data["image"]
            bbox = img_data["bbox"]

            # Добавляем задержку перед вставкой каждого изображения
            print(f"Ожидание 10 секунд перед вставкой изображения {i + 1}...")
            time.sleep(30)  # Задержка в 10 секунд

            # Вставляем изображение в PDF
            new_page = new_doc.load_page(i)  # загружаем соответствующую страницу
            rect = fitz.Rect(bbox)  # Координаты для вставки изображения
            img_bytes = BytesIO()
            image.save(img_bytes, format="PNG")
            img_bytes.seek(0)

            # Вставляем изображение в указанное место
            new_page.insert_image(rect, stream=img_bytes)

        # Сохраняем новый PDF с изображениями
        new_pdf_path = f"/content/updated_with_images_{uuid.uuid4()}.pdf"
        new_doc.save(new_pdf_path)
        print(f"Изображения вставлены, новый файл: {new_pdf_path}")

if __name__ == "__main__":
    pdf_url = "/content/final_pdf_with_text (8).pdf"  # Путь к PDF файлу
    app = PDFEditor(pdf_url)


FileUpload(value={}, accept='.pdf', description='Upload')

Button(description='Внести правки', disabled=True, style=ButtonStyle())

Button(description='Сохранить изменения', disabled=True, style=ButtonStyle())

Button(description='Обновить', style=ButtonStyle())

Text(value='', layout=Layout(width='50%'), placeholder='Введите закодированный текст для поиска')

Button(description='Найти', style=ButtonStyle())

FileNotFoundError: no such file: '/content/updated_1613fc55-f6fb-4efe-bbb6-2ef6242765be.pdf'

In [107]:
import fitz  # PyMuPDF
import ipywidgets as widgets
from IPython.display import display
import os
import uuid
from pdf2docx import Converter
from docx import Document
import shutil
from io import BytesIO
from PIL import Image
import time  # Для добавления задержки

class PDFEditor:
    def __init__(self, pdf_url=None):
        self.pdf_path = ""
        self.text_blocks = []  # Список текстовых блоков с координатами
        self.text_coords = []  # Список координат для текста
        self.images = []  # Список для хранения изображений и их координат
        self.raw_text = ""
        self.temp_pdf_path = None
        self.word_file_path = None

        # Загрузка PDF
        self.upload_button = widgets.FileUpload(accept='.pdf', multiple=False)
        self.upload_button.observe(self.load_pdf, names='value')

        # Кнопки
        self.edit_button = widgets.Button(description="Внести правки", disabled=True)
        self.edit_button.on_click(self.extract_text)

        self.save_button = widgets.Button(description="Сохранить изменения", disabled=True)
        self.save_button.on_click(self.save_pdf)

        self.refresh_button = widgets.Button(description="Обновить", disabled=False)
        self.refresh_button.on_click(self.refresh_text)

        # Текстовые поля
        self.encoded_text = widgets.Textarea(layout=widgets.Layout(width='50%', height='500px'))
        self.decoded_text = widgets.HTML(layout=widgets.Layout(width='50%', height='500px'))

        # Поиск
        self.search_input = widgets.Text(placeholder="Введите закодированный текст для поиска", layout=widgets.Layout(width='50%'))
        self.search_button = widgets.Button(description="Найти", disabled=False)
        self.search_button.on_click(self.search_and_highlight)

        # Отображение
        display(self.upload_button, self.edit_button, self.save_button, self.refresh_button)
        display(self.search_input, self.search_button)
        display(widgets.HBox([self.encoded_text, self.decoded_text]))

        if pdf_url:
            self.download_pdf(pdf_url)

    def download_pdf(self, url):
        filename = "/content/final_pdf_with_text (8).pdf"
        os.system(f"wget -O {filename} {url}")
        self.pdf_path = filename
        self.edit_button.disabled = False

    def load_pdf(self, change):
        if self.upload_button.value:
            self.pdf_path = list(self.upload_button.value.keys())[0]
            self.edit_button.disabled = False

    def extract_text(self, event):
        if not self.pdf_path:
            return

        # Извлекаем текст и координаты из оригинального PDF с помощью PyMuPDF
        self.text_blocks = []
        self.text_coords = []
        self.images = []
        self.raw_text = ""

        doc = fitz.open(self.pdf_path)

        for page_num in range(len(doc)):
            page = doc.load_page(page_num)
            blocks = page.get_text("dict")["blocks"]
            for block in blocks:
                if block["type"] == 0:  # Это текстовый блок
                    for line in block["lines"]:
                        for span in line["spans"]:
                            text = span["text"]
                            bbox = span["bbox"]  # Координаты блока текста
                            self.text_blocks.append({"text": text, "bbox": bbox})
                            self.raw_text += text + "\n"

            # Извлекаем изображения
            for img_index, img in enumerate(page.get_images(full=True)):
                xref = img[0]
                base_image = doc.extract_image(xref)
                image_bytes = base_image["image"]
                image = Image.open(BytesIO(image_bytes))
                self.images.append({"image": image, "bbox": img[1]})

        # Отображаем извлечённый текст в кодированном и нормальном виде
        self.encoded_text.value = self.encode_text(self.raw_text)
        self.decoded_text.value = self.raw_text

        # Сохраняем путь к временной копии PDF
        self.temp_pdf_path = "/content/temp_copy.pdf"
        shutil.copy(self.pdf_path, self.temp_pdf_path)

        # Разрешаем сохранить файл
        self.save_button.disabled = False

    def encode_text(self, text):
        encoded_text = text.encode('utf-8')
        return ' '.join([f'\\x{b:02x}' for b in encoded_text])

    def search_and_highlight(self, event):
        search_term = self.search_input.value

        if search_term:
            decoded_search_term = self.decode_encoded_text(search_term)
            self.decoded_selected_text = decoded_search_term
            self.update_highlighted_text()

    def decode_encoded_text(self, encoded_text):
        encoded_bytes = bytes([int(b, 16) for b in encoded_text.split("\\x")[1:] if b])
        decoded_text = encoded_bytes.decode('utf-8', errors='ignore')
        return decoded_text

    def update_highlighted_text(self):
        if self.decoded_selected_text:
            highlighted_text = self.highlight_text_in_html(self.raw_text, self.decoded_selected_text)
            self.decoded_text.value = highlighted_text
        else:
            self.decoded_text.value = self.raw_text

    def highlight_text_in_html(self, text, selected_text):
        if selected_text:
            highlighted = f'<span style="background-color: yellow;">{selected_text}</span>'
            return text.replace(selected_text, highlighted)
        return text

    def refresh_text(self, event):
        # Обновление текста в правом окне после изменения в левом
        self.decoded_text.value = self.encoded_text.value

    def save_pdf(self, event):
        if not self.temp_pdf_path:
            return

        # Сохраняем изменения в Word
        doc = Document()
        doc.add_paragraph(self.decode_encoded_text(self.encoded_text.value))

        word_temp_path = f"/content/updated_{uuid.uuid4()}.docx"
        doc.save(word_temp_path)

        # Конвертируем Word обратно в PDF
        new_pdf_path = f"/content/updated_{uuid.uuid4()}.pdf"
        os.system(f"libreoffice --headless --convert-to pdf {word_temp_path} --outdir /content")

        # Проверим, что файл был создан
        if not os.path.exists(new_pdf_path):
            print(f"Ошибка: файл {new_pdf_path} не был создан.")
            return

        # Вставляем изображения в новый PDF на тех же координатах с задержкой
        self.insert_images(new_pdf_path)

        print(f"Файл сохранён как {new_pdf_path}")

    def insert_images(self, pdf_path):
        # Открываем новый PDF
        new_doc = fitz.open(pdf_path)

        # Вставляем изображения на соответствующие места с задержкой
        for i, img_data in enumerate(self.images):
            image = img_data["image"]
            bbox = img_data["bbox"]

            # Вставляем изображение в PDF
            new_page = new_doc.load_page(i)  # загружаем соответствующую страницу
            rect = fitz.Rect(bbox)  # Координаты для вставки изображения
            img_bytes = BytesIO()
            image.save(img_bytes, format="PNG")
            img_bytes.seek(0)

            # Вставляем изображение в указанное место
            new_page.insert_image(rect, stream=img_bytes)

        # Сохраняем новый PDF с изображениями
        new_pdf_path_with_images = f"/content/updated_with_images_{uuid.uuid4()}.pdf"
        new_doc.save(new_pdf_path_with_images)
        print(f"Изображения вставлены, новый файл: {new_pdf_path_with_images}")

if __name__ == "__main__":
    pdf_url = "/content/final_pdf_with_text (8).pdf"  # Путь к PDF файлу
    app = PDFEditor(pdf_url)


FileUpload(value={}, accept='.pdf', description='Upload')

Button(description='Внести правки', disabled=True, style=ButtonStyle())

Button(description='Сохранить изменения', disabled=True, style=ButtonStyle())

Button(description='Обновить', style=ButtonStyle())

Text(value='', layout=Layout(width='50%'), placeholder='Введите закодированный текст для поиска')

Button(description='Найти', style=ButtonStyle())

Ошибка: файл /content/updated_c1f8000e-6374-4414-b3b2-3b98940f1f3d.pdf не был создан.


In [ ]:
#!apt update
#!apt install -y libreoffice
#!pip install pdf2docx python-docx ipywidgets fitz

import fitz  # PyMuPDF
import ipywidgets as widgets
from IPython.display import display
import os
import uuid
from pdf2docx import Converter
from docx import Document
import shutil

class PDFEditor:
    def __init__(self, pdf_url=None):
        self.pdf_path = ""
        self.text_blocks = []  # Список текстовых блоков с координатами
        self.text_coords = []  # Список координат для текста
        self.raw_text = ""
        self.temp_pdf_path = None
        self.word_file_path = None
        self.images = []  # Список изображений

        # Загрузка PDF
        self.upload_button = widgets.FileUpload(accept='.pdf', multiple=False)
        self.upload_button.observe(self.load_pdf, names='value')

        # Кнопки
        self.edit_button = widgets.Button(description="Внести правки", disabled=True)
        self.edit_button.on_click(self.extract_text)

        self.save_button = widgets.Button(description="Сохранить изменения", disabled=True)
        self.save_button.on_click(self.save_pdf)

        self.refresh_button = widgets.Button(description="Обновить", disabled=False)
        self.refresh_button.on_click(self.refresh_text)

        # Текстовые поля
        self.encoded_text = widgets.Textarea(layout=widgets.Layout(width='50%', height='500px'))
        self.decoded_text = widgets.HTML(layout=widgets.Layout(width='50%', height='500px'))

        # Поиск
        self.search_input = widgets.Text(placeholder="Введите закодированный текст для поиска", layout=widgets.Layout(width='50%'))
        self.search_button = widgets.Button(description="Найти", disabled=False)
        self.search_button.on_click(self.search_and_highlight)

        # Отображение
        display(self.upload_button, self.edit_button, self.save_button, self.refresh_button)
        display(self.search_input, self.search_button)
        display(widgets.HBox([self.encoded_text, self.decoded_text]))

        if pdf_url:
            self.download_pdf(pdf_url)

    def download_pdf(self, url):
        filename = "/content/final_pdf_with_text (8).pdf"
        os.system(f"wget -O {filename} {url}")
        self.pdf_path = filename
        self.edit_button.disabled = False

    def load_pdf(self, change):
        if self.upload_button.value:
            self.pdf_path = list(self.upload_button.value.keys())[0]
            self.edit_button.disabled = False

    def extract_text(self, event):
        if not self.pdf_path:
            return

        # Извлекаем текст и координаты из оригинального PDF с помощью PyMuPDF
        self.text_blocks = []
        self.text_coords = []
        self.raw_text = ""
        self.images = []

        doc = fitz.open(self.pdf_path)

        for page_num in range(len(doc)):
            page = doc.load_page(page_num)
            blocks = page.get_text("dict")["blocks"]
            for block in blocks:
                if block["type"] == 0:  # Это текстовый блок
                    for line in block["lines"]:
                        for span in line["spans"]:
                            text = span["text"]
                            bbox = span["bbox"]  # Координаты блока текста
                            self.text_blocks.append({"text": text, "bbox": bbox})
                            self.raw_text += text + "\n"

                elif block["type"] == 1:  # Это изображение
                    img = block["image"]
                    image_path = f"/content/image_{uuid.uuid4().hex}.png"
                    with open(image_path, "wb") as img_file:
                        img_file.write(img["image"])

                    self.images.append({"image_path": image_path, "bbox": block["bbox"]})

        # Отображаем извлечённый текст в кодированном и нормальном виде
        self.encoded_text.value = self.encode_text(self.raw_text)
        self.decoded_text.value = self.raw_text

        # Сохраняем путь к временной копии PDF
        self.temp_pdf_path = "/content/temp_copy.pdf"
        shutil.copy(self.pdf_path, self.temp_pdf_path)

        # Разрешаем сохранить файл
        self.save_button.disabled = False

    def encode_text(self, text):
        encoded_text = text.encode('utf-8')
        return ' '.join([f'\\x{b:02x}' for b in encoded_text])

    def search_and_highlight(self, event):
        search_term = self.search_input.value

        if search_term:
            decoded_search_term = self.decode_encoded_text(search_term)
            self.decoded_selected_text = decoded_search_term
            self.update_highlighted_text()

    def decode_encoded_text(self, encoded_text):
        encoded_bytes = bytes([int(b, 16) for b in encoded_text.split("\\x")[1:] if b])
        decoded_text = encoded_bytes.decode('utf-8', errors='ignore')
        return decoded_text

    def update_highlighted_text(self):
        if self.decoded_selected_text:
            highlighted_text = self.highlight_text_in_html(self.raw_text, self.decoded_selected_text)
            self.decoded_text.value = highlighted_text
        else:
            self.decoded_text.value = self.raw_text

    def highlight_text_in_html(self, text, selected_text):
        if selected_text:
            highlighted = f'<span style="background-color: yellow;">{selected_text}</span>'
            return text.replace(selected_text, highlighted)
        return text

    def refresh_text(self, event):
        # Обновление текста в правом окне после изменения в левом
        self.decoded_text.value = self.encoded_text.value

    def save_pdf(self, event):
        if not self.temp_pdf_path:
            return

        # Сохраняем изменения в Word
        doc = Document()
        doc.add_paragraph(self.decode_encoded_text(self.encoded_text.value))

        # Добавляем изображения из оригинального PDF в Word
        for img in self.images:
            image_path = img["image_path"]
            doc.add_picture(image_path)

        word_temp_path = "/content/updated_word.docx"
        doc.save(word_temp_path)

        # Конвертируем Word обратно в PDF с заданным именем
        new_pdf_path = "/content/EYSPDF_YRA.pdf"
        os.system(f"libreoffice --headless --convert-to pdf {word_temp_path} --outdir /content")

        print(f"Файл сохранён как {new_pdf_path}")


if __name__ == "__main__":
    pdf_url = "/content/final_pdf_with_text (8).pdf"  # Путь к PDF файлу
    app = PDFEditor(pdf_url)
